# Cystisoma corneas

## Inference

First open your heatmap in napari. 

In [6]:
# import modules
import torchio as tio

# load in the nifti file with torchio
# 2nd scan
# image_path = '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii'

# Poor scans (not used)
#image_path = '/media/jake/2tb_ssd/mctv_data/Cystisoma_1448930_head/Cystisoma_1448930_head0.nii'
#image_path = '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190212_01_head/FEG20190212_010.nii'
# image_path = '/media/jake/2tb_ssd/mctv_data/Cystisoma_sp_FEG221129_366/FEG221129_366.nii'
# image = tio.ScalarImage(image_path)



In [7]:
image

ScalarImage(shape: (1, 1446, 1657, 1964); spacing: (1.00, 1.00, 1.00); orientation: LPS+; path: "/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii")

In [8]:
# view file with napari
import napari


viewer = napari.view_image(image.numpy(), name='image')


/home/jake/projects/dhr/venv/lib/python3.9/site-packages/napari/layers/base/base.py:1540: RuntimeWarning: invalid value encountered in cast
  corners[:, displayed_axes] = data_bbox_clipped
/home/jake/projects/dhr/venv/lib/python3.9/site-packages/napari/layers/base/base.py:1540: RuntimeWarning: invalid value encountered in cast
  corners[:, displayed_axes] = data_bbox_clipped
/home/jake/projects/dhr/venv/lib/python3.9/site-packages/napari/layers/base/base.py:1540: RuntimeWarning: invalid value encountered in cast
  corners[:, displayed_axes] = data_bbox_clipped


In napari, label a few of the features (that are next to each other) to estimate the resample ratio, then save it as a csv file and load it in the next step


In [18]:
import pandas as pd
# 2nd scan
#RR = pd.read_csv('/home/jake/projects/dhr/FEG20190213_01_corneas_resample_ratio.csv')
# 3rd scan
RR = pd.read_csv('/home/jake/projects/dhr/Cystisoma_sp_FEG221129_366_corneas_estimating_resample_ratio.csv')

RR

index  axis-0  axis-1      axis-2      axis-3
0     0.0     0.0   643.0  780.704145  299.347616
1     1.0     0.0   643.0  793.346004  317.046218
2     2.0     0.0   643.0  808.516233  336.009005
3     3.0     0.0   643.0  828.111113  354.339699
4     4.0     0.0   643.0  847.073901  374.566672
5     5.0     0.0   643.0  866.668781  389.736902
6     6.0     0.0   643.0  919.132492  394.793645
7     7.0     0.0   643.0  893.216683  380.887601
8     8.0     0.0   643.0  871.093431  363.189000
9     9.0     0.0   643.0  852.130644  345.490398
10   10.0     0.0   643.0  834.432042  327.159704
11   11.0     0.0   643.0  818.629720  308.829010
12   12.0     0.0   643.0  805.355769  291.130408
13   13.0     0.0   643.0  792.081818  272.167621
14   14.0     0.0   643.0  805.987862  254.469020
15   15.0     0.0   643.0  814.837162  267.110878
16   16.0     0.0   643.0  830.007392  282.913201
17   17.0     0.0   643.0  841.385064  301.243895

In [19]:
from scipy.spatial import distance_matrix

coordinates = RR[['axis-1', 'axis-2', 'axis-3']].values
dist_matrix = distance_matrix(coordinates, coordinates) #Create a distance matrix


In [20]:
import numpy as np
np.fill_diagonal(dist_matrix, np.inf)

# Find the nearest neighbor distance for each point
nearest_distances = np.min(dist_matrix, axis=1)

# Add the nearest distances to the dataframe
RR['nearest_distance'] = nearest_distances
RR

index  axis-0  axis-1      axis-2      axis-3  nearest_distance
0     0.0     0.0   643.0  780.704145  299.347616         21.749875
1     1.0     0.0   643.0  793.346004  317.046218         21.749875
2     2.0     0.0   643.0  808.516233  336.009005         24.284216
3     3.0     0.0   643.0  828.111113  354.339699         25.597812
4     4.0     0.0   643.0  847.073901  374.566672         24.780944
5     5.0     0.0   643.0  866.668781  389.736902         24.780944
6     6.0     0.0   643.0  919.132492  394.793645         29.411005
7     7.0     0.0   643.0  893.216683  380.887601         27.983946
8     8.0     0.0   643.0  871.093431  363.189000         25.938924
9     9.0     0.0   643.0  852.130644  345.490398         25.480480
10   10.0     0.0   643.0  834.432042  327.159704         24.201813
11   11.0     0.0   643.0  818.629720  308.829010         22.123252
12   12.0     0.0   643.0  805.355769  291.130408         22.123252
13   13.0     0.0   643.0  792.081818  272.167621         22.508189
14   14.0     0.0   643.0  805.987862  254.469020         15.431354
15   15.0     0.0   643.0  814.837162  267.110878         15.431354
16   16.0     0.0   643.0  830.007392  282.913201         21.574656
17   17.0     0.0   643.0  841.385064  301.243895         21.574656

In [21]:
mean_nearest_distance = RR['nearest_distance'].mean()
mean_nearest_distance

23.151474885249055

In [22]:
resample_ratio = mean_nearest_distance/10 #Makes average distance between features 10 voxels
resample_ratio

2.3151474885249055

## Inference

In [5]:
!python main.py infer -h #If you need help for parameters in infer

usage: main.py [-h] [--volume_path VOLUME_PATH]
               [--sql_storage_url SQL_STORAGE_URL]
               [--starting_weights_path STARTING_WEIGHTS_PATH]
               [--model_path MODEL_PATH] [--profile] [--num_steps NUM_STEPS]
               [--check_val_every_n_epoch CHECK_VAL_EVERY_N_EPOCH]
               [--resample_ratio_path RESAMPLE_RATIO_PATH]
               [--bbox_path BBOX_PATH] [--n_x_dirs N_X_DIRS]
               [--n_y_dirs N_Y_DIRS] [--n_z_dirs N_Z_DIRS]
               [--resample_ratio RESAMPLE_RATIO] [--already_resampled]
               [--training_data_histogram] [--infer_with_max_filter_fun]
               [--average_threshold AVERAGE_THRESHOLD]
               [--inference_peak_min_val INFERENCE_PEAK_MIN_VAL]
               {train,tune,infer,locate_peaks} config_path

Train, hyperparameter tune or infer with a deep heatmap regression model

positional arguments:
  {train,tune,infer,locate_peaks}
                        Mode of operation
  config_path      

Make inference first with 1 direction in the x, y, and z axis before creating inference in 3 directions. This will produce three files: two csv files (one for the resampled space, and the other not), and a nifty file with predictions.

*Note: these files are currently saved to /home/jake/projects/dhr/output/

In [1]:
#Inference with 1 direction in x, y, and z for 2nd scan
#!python main.py infer configs/cystisoma_corneas.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m .logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 1 -ny 1 -nz 1

#3rd scan
!python main.py infer configs/cystisoma_corneas.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_sp_FEG221129_366/FEG221129_366.nii' -m ./logs/cystisoma_corneas/lightning_logs/version_14/ -rr 2.3151474885249055 -nx 1 -ny 1 -nz 1

TorchIO version: 0.18.88
Running setup!
Found 2 labelled images with labels in ./dataset/cystisoma_corneas/whole/train_images_10/ and ./dataset/cystisoma_corneas/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/cystisoma_corneas/whole/train_images_10/ and ./dataset/cystisoma_corneas/whole/train_labels_10/ for analysis
Training:   2
Validation:  2
Test:       2
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_length': 9, 'batch_size': 2, "
 "'config_stem': 'cystisoma_corneas', 'correct_prediction_distance': 6, "
 "'debug_plots': False, 'double_channels_with_depth': True, 'dropout': "
 "0.0175756794552526, 'heatmap_max_length': 64, 'histogra

You can then try in more directions (3 direction in x, y, z is usually best) and modify parameters such as max filter (-mxf) (although this usually doesn't work well with Cystisoma), average threshold (-at), and peak minimum values (-ipmv).

In [ ]:
#Attempts of inferences for 2nd scan (best model should be found on last commented line in this kernel)
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 1
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 1.5
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 2
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.5
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.5 --infer_with_max_filter_fun
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.5 
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.5 
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.5 
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.5 --infer_with_max_filter_fun
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.5 --infer_with_max_filter_fun
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.5 --infer_with_max_filter_fun
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.01 
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.02
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.03
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.04 
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.05
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.1
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.2 
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.3 
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.4
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.5 --infer_with_max_filter_fun
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.02 --infer_with_max_filter_fun
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.15 -at 0.02 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.02 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.03 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.15 -at 0.03 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.03 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.02 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.15 -at 0.02 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.02 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.03 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.15 -at 0.03 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.03 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.01 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.15 -at 0.01 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.01 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.01 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.15 -at 0.01 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.01
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.02 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.02 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.02 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.02 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.02 
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.02
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.4 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.3 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.2 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.1 --infer_with_max_filter_fun
# !python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.05 --infer_with_max_filter_fun


#Best inference for 2nd scan
#!python main.py infer configs/cystisoma_corneas.yaml -v /media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii -m ./logs/cystisoma_corneas/lightning_logs/version_13/ -rr 2.588516765563356 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.5 

In [3]:
#Scan 3 (not used)
# !python main.py infer configs/cystisoma_corneas.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_sp_FEG221129_366/FEG221129_366.nii' -m ./logs/cystisoma_corneas/lightning_logs/version_14/ -rr 2.3151474885249055 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.5

TorchIO version: 0.18.88
Running setup!
Found 2 labelled images with labels in ./dataset/cystisoma_corneas/whole/train_images_10/ and ./dataset/cystisoma_corneas/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/cystisoma_corneas/whole/train_images_10/ and ./dataset/cystisoma_corneas/whole/train_labels_10/ for analysis
Training:   2
Validation:  2
Test:       2
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_length': 9, 'batch_size': 2, "
 "'config_stem': 'cystisoma_corneas', 'correct_prediction_distance': 6, "
 "'debug_plots': False, 'double_channels_with_depth': True, 'dropout': "
 "0.0175756794552526, 'heatmap_max_length': 64, 'histogra

 37%|███████████████▊                           | 36/98 [00:18<00:31,  1.98it/s]


 38%|████████████████▏                          | 37/98 [00:19<00:30,  1.98it/s]


 39%|████████████████▋                          | 38/98 [00:19<00:30,  1.94it/s]


 40%|█████████████████                          | 39/98 [00:20<00:30,  1.94it/s]


 41%|█████████████████▌                         | 40/98 [00:20<00:29,  1.94it/s]


 42%|█████████████████▉                         | 41/98 [00:21<00:29,  1.96it/s]


 43%|██████████████████▍                        | 42/98 [00:21<00:28,  1.98it/s]


 44%|██████████████████▊                        | 43/98 [00:22<00:27,  1.99it/s]


 45%|███████████████████▎                       | 44/98 [00:22<00:27,  1.99it/s]


 46%|███████████████████▋                       | 45/98 [00:23<00:26,  2.00it/s]


 47%|████████████████████▏                      | 46/98 [00:23<00:25,  2.00it/s]


 48%|████████████████████▌                      | 47/98 [00:24<00:25,  2.00it/s]


 49%

  4%|█▊                                          | 4/98 [00:02<00:48,  1.93it/s]


  5%|██▏                                         | 5/98 [00:02<00:47,  1.95it/s]


  6%|██▋                                         | 6/98 [00:03<00:46,  1.98it/s]


  7%|███▏                                        | 7/98 [00:03<00:45,  1.99it/s]


  8%|███▌                                        | 8/98 [00:04<00:45,  2.00it/s]


  9%|████                                        | 9/98 [00:04<00:44,  2.00it/s]


 10%|████▍                                      | 10/98 [00:05<00:43,  2.00it/s]


 11%|████▊                                      | 11/98 [00:05<00:43,  2.00it/s]


 12%|█████▎                                     | 12/98 [00:06<00:42,  2.01it/s]


 13%|█████▋                                     | 13/98 [00:06<00:42,  2.01it/s]


 14%|██████▏                                    | 14/98 [00:07<00:41,  2.01it/s]


 15%|██████▌                                    | 15/98 [00:07<00:41,  2.01it/s]


 16%

 80%|██████████████████████████████████▏        | 78/98 [00:39<00:10,  1.98it/s]


 81%|██████████████████████████████████▋        | 79/98 [00:39<00:09,  1.97it/s]


 82%|███████████████████████████████████        | 80/98 [00:40<00:09,  1.97it/s]


 83%|███████████████████████████████████▌       | 81/98 [00:40<00:08,  1.97it/s]


 84%|███████████████████████████████████▉       | 82/98 [00:41<00:08,  1.98it/s]


 85%|████████████████████████████████████▍      | 83/98 [00:41<00:07,  1.97it/s]


 86%|████████████████████████████████████▊      | 84/98 [00:42<00:07,  1.97it/s]


 87%|█████████████████████████████████████▎     | 85/98 [00:42<00:06,  1.98it/s]


 88%|█████████████████████████████████████▋     | 86/98 [00:43<00:06,  1.97it/s]


 89%|██████████████████████████████████████▏    | 87/98 [00:43<00:05,  1.97it/s]


 90%|██████████████████████████████████████▌    | 88/98 [00:44<00:05,  1.98it/s]


 91%|███████████████████████████████████████    | 89/98 [00:44<00:04,  1.98it/s]


 92%

 47%|████████████████████▏                      | 46/98 [00:23<00:26,  1.99it/s]


 48%|████████████████████▌                      | 47/98 [00:23<00:25,  1.99it/s]


 49%|█████████████████████                      | 48/98 [00:24<00:25,  1.99it/s]


 50%|█████████████████████▌                     | 49/98 [00:24<00:24,  1.99it/s]


 51%|█████████████████████▉                     | 50/98 [00:25<00:24,  1.99it/s]


 52%|██████████████████████▍                    | 51/98 [00:25<00:23,  1.99it/s]


 53%|██████████████████████▊                    | 52/98 [00:26<00:23,  1.99it/s]


 54%|███████████████████████▎                   | 53/98 [00:26<00:22,  1.99it/s]


 55%|███████████████████████▋                   | 54/98 [00:27<00:22,  2.00it/s]


 56%|████████████████████████▏                  | 55/98 [00:27<00:21,  1.99it/s]


 57%|████████████████████████▌                  | 56/98 [00:28<00:21,  1.98it/s]


 58%|█████████████████████████                  | 57/98 [00:28<00:21,  1.94it/s]


 59%

...

  9%|████                                        | 9/98 [00:04<00:44,  2.00it/s]


 10%|████▍                                      | 10/98 [00:05<00:43,  2.00it/s]


 11%|████▊                                      | 11/98 [00:05<00:43,  2.01it/s]


 12%|█████▎                                     | 12/98 [00:06<00:42,  2.01it/s]


 13%|█████▋                                     | 13/98 [00:06<00:42,  2.01it/s]


 14%|██████▏                                    | 14/98 [00:07<00:41,  2.01it/s]


 15%|██████▌                                    | 15/98 [00:07<00:41,  2.01it/s]


 16%|███████                                    | 16/98 [00:08<00:40,  2.01it/s]


 17%|███████▍                                   | 17/98 [00:08<00:40,  2.01it/s]


 18%|███████▉                                   | 18/98 [00:09<00:39,  2.01it/s]


 19%|████████▎                                  | 19/98 [00:09<00:39,  2.01it/s]


 20%|████████▊                                  | 20/98 [00:10<00:38,  2.01it/s]


 21%

Rotating volume back to original orientation...


100%|█████████████████████████████████████████████| 3/3 [03:54<00:00, 78.31s/it]

                                                                                
 33%|██████████████▋                             | 1/3 [03:54<07:49, 234.50s/it]

  0%|                                                     | 0/3 [00:00<?, ?it/s]
Running inference with 120° rotation along the x-axis (3/3),
60° rotation along the y-axis (2/3)
and 0° rotation along the z-axis (1/3)
Creating sampler and applying transform to image...
Initialising patch_loader and aggregator...
Starting inference...



  0%|                                                    | 0/98 [00:00<?, ?it/s]


  1%|▍                                           | 1/98 [00:00<01:02,  1.54it/s]


  2%|▉                                           | 2/98 [00:01<00:53,  1.78it/s]


  3%|█▎                                          | 3/98 [00:01<00:50,  1.88it/s]


  4%|█▊                            

 67%|████████████████████████████▉              | 66/98 [00:33<00:16,  1.98it/s]


 68%|█████████████████████████████▍             | 67/98 [00:33<00:15,  1.98it/s]


 69%|█████████████████████████████▊             | 68/98 [00:34<00:15,  1.99it/s]


 70%|██████████████████████████████▎            | 69/98 [00:34<00:14,  1.99it/s]


 71%|██████████████████████████████▋            | 70/98 [00:35<00:14,  1.99it/s]


 72%|███████████████████████████████▏           | 71/98 [00:35<00:13,  2.00it/s]


 73%|███████████████████████████████▌           | 72/98 [00:36<00:13,  1.99it/s]


 74%|████████████████████████████████           | 73/98 [00:36<00:12,  2.00it/s]


 76%|████████████████████████████████▍          | 74/98 [00:37<00:12,  2.00it/s]


 77%|████████████████████████████████▉          | 75/98 [00:37<00:11,  1.99it/s]


 78%|█████████████████████████████████▎         | 76/98 [00:38<00:11,  1.99it/s]


 79%|█████████████████████████████████▊         | 77/98 [00:38<00:10,  1.99it/s]


 80%

 34%|██████████████▍                            | 33/98 [00:16<00:32,  2.00it/s]


 35%|██████████████▉                            | 34/98 [00:17<00:32,  2.00it/s]


 36%|███████████████▎                           | 35/98 [00:17<00:31,  2.00it/s]


 37%|███████████████▊                           | 36/98 [00:18<00:30,  2.00it/s]


 38%|████████████████▏                          | 37/98 [00:18<00:30,  2.00it/s]


 39%|████████████████▋                          | 38/98 [00:19<00:29,  2.01it/s]


 40%|█████████████████                          | 39/98 [00:19<00:29,  2.01it/s]


 41%|█████████████████▌                         | 40/98 [00:20<00:28,  2.01it/s]


 42%|█████████████████▉                         | 41/98 [00:20<00:28,  2.01it/s]


 43%|██████████████████▍                        | 42/98 [00:21<00:28,  1.99it/s]


 44%|██████████████████▊                        | 43/98 [00:21<00:27,  2.00it/s]


 45%|███████████████████▎                       | 44/98 [00:22<00:26,  2.00it/s]


 46%

  3%|█▎                                          | 3/98 [00:01<00:50,  1.90it/s]


  4%|█▊                                          | 4/98 [00:02<00:48,  1.94it/s]


  5%|██▏                                         | 5/98 [00:02<00:47,  1.97it/s]


  6%|██▋                                         | 6/98 [00:03<00:46,  1.99it/s]


  7%|███▏                                        | 7/98 [00:03<00:45,  1.99it/s]


  8%|███▌                                        | 8/98 [00:04<00:44,  2.00it/s]


  9%|████                                        | 9/98 [00:04<00:44,  2.00it/s]


 10%|████▍                                      | 10/98 [00:05<00:43,  2.01it/s]


 11%|████▊                                      | 11/98 [00:05<00:43,  2.01it/s]


 12%|█████▎                                     | 12/98 [00:06<00:42,  2.01it/s]


 13%|█████▋                                     | 13/98 [00:06<00:42,  2.01it/s]


 14%|██████▏                                    | 14/98 [00:07<00:41,  2.01it/s]


 15%

You can then view your inference in napari. It might be useful to you, especially if you are trying many inferences with modified parameters, to evalute the performance of each and track estimated % of correct and incorrect inference points in an Excel spreadsheet for example.

In [4]:
import napari
import numpy as np
import torchio as tio


image_path = '/media/jake/2tb_ssd/mctv_data/Cystisoma_sp_FEG221129_366/FEG221129_366.nii'
image = tio.ScalarImage(image_path)

heatmap_path = '/home/jake/projects/dhr/output/FEG221129_366.logs_cystisoma_corneas_lightning_logs_version_14_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction.nii'
#Make sure to use resampled space csv here.
y_hat_path = '/home/jake/projects/dhr/output/FEG221129_366.logs_cystisoma_corneas_lightning_logs_version_14_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction_peak_min_val_0_5_method_center_of_mass.resampled_space_peaks.csv'
heatmap = tio.ScalarImage(heatmap_path)


viewer = napari.view_image(heatmap.numpy(), name='heatmap', contrast_limits=[0, 1])
#viewer.add_image(image.numpy(), name='image')

# load the coordinates to analyse
def load_coordinates(path, flip_axes=False, mct_path=None):
    locations = np.loadtxt(
        path,
        delimiter=',',
        ndmin=2,
        dtype=np.float64
    )
    if not flip_axes: 
        return locations.tolist()

    if not mct_path:
        raise Exception('You must specify `mct_path` if you need to flip_axes')

    mct = tio.ScalarImage(mct_path)
    locations[:,0] = mct.shape[1] - locations[:,0]
    locations[:,1] = mct.shape[2] - locations[:,1]

    return locations.tolist()


y_hat = load_coordinates(y_hat_path)


viewer.add_points(y_hat)


<Points layer 'Points' at 0x7fb85c398370>

## Modifying inference

In software such as MatLab you can modify the inference made from your model by adding and deleting points. This will be useful in retraining your model later.

##  (Re)training 

In [5]:
# We trained this model on a single scan, ran inference on it and then manually checked the labels. Now we are adding that labelled data to the dataset and retraining the model
# python check_data.py configs/cystisoma_corneas.yaml
# after updating the config to train for another 100,000 steps
# and changing the sigma from 2.5 to 2 (to suit the new data)
!python main.py train configs/cystisoma_corneas.yaml -w ./logs/cystisoma_corneas/lightning_logs/version_13/checkpoints/epoch=2809-step=699520.ckpt -ne 10

TorchIO version: 0.18.88
("Initiating model using the following config: {'seed': 44, 'lr': "
 "0.0424937961824346, 'num_steps': 800000, 'weight_decay': "
 "1.52709371682483e-06, 'momentum': 0.510999549987835, 'nesterov': False, "
 "'act': 'ReLU', 'output_activation': 'None', 'softargmax': False, "
 "'num_encoding_blocks': 5, 'out_channels_first_layer': 32, "
 "'double_channels_with_depth': True, 'pooling_type': 'max', "
 "'upsampling_type': 'conv', 'dropout': 0.0175756794552526, "
 "'loss_in_sigma_space': False, 'debug_plots': False, 'mse_with_f1': False, "
 "'visualise_model': False, 'learn_sigma': False, 'optimiser': 'SGD', "
 "'pin_memory': False, 'train_images_dir': "
 "'./dataset/cystisoma_corneas/whole/train_images_10/', 'train_labels_dir': "
 "'./dataset/cystisoma_corneas/whole/train_labels_10/', 'test_images_dir': "
 "'./dataset/cystisoma_corneas/whole/train_images_10/', 'test_labels_dir': "
 "'./dataset/cystisoma_corneas/whole/train_labels_10/', 'image_suffix': "
 "'image', 'l

# Cystisoma rhabdoms

## Checking

Check hyperparameters for heatmap. Modify these need be.

In [ ]:
!python check_data.py ./configs/cystisoma_rhabdoms.yaml

In [12]:
!python check_data.py -h

usage: check_data.py [-h] [--n_plot_at_once N_PLOT_AT_ONCE] [--check-loading]
                     config_path

positional arguments:
  config_path           The path to the config file. Example:
                        configs/fiddlercrab_cornea_config.yaml

options:
  -h, --help            show this help message and exit
  --n_plot_at_once N_PLOT_AT_ONCE
                        The number of images to plot at once.
  --check-loading       Check loading of all images and labels, but don't plot
                        anything. Can be useful if you just want to make sure
                        everything loads correctly. Will print an error
                        message if a image or label does not load correctly.


## (Re)training

After you finsihing checking the model you can train the model to rhabdoms and extend number of steps. 

In [2]:
#If you want to see all arguments 
!python main.py train -h

usage: main.py [-h] [--volume_path VOLUME_PATH]
               [--sql_storage_url SQL_STORAGE_URL]
               [--starting_weights_path STARTING_WEIGHTS_PATH]
               [--model_path MODEL_PATH] [--profile] [--num_steps NUM_STEPS]
               [--check_val_every_n_epoch CHECK_VAL_EVERY_N_EPOCH]
               [--resample_ratio_path RESAMPLE_RATIO_PATH]
               [--bbox_path BBOX_PATH] [--n_x_dirs N_X_DIRS]
               [--n_y_dirs N_Y_DIRS] [--n_z_dirs N_Z_DIRS]
               [--resample_ratio RESAMPLE_RATIO] [--already_resampled]
               [--training_data_histogram] [--infer_with_max_filter_fun]
               [--average_threshold AVERAGE_THRESHOLD]
               [--inference_peak_min_val INFERENCE_PEAK_MIN_VAL]
               {train,tune,infer,locate_peaks} config_path

Train, hyperparameter tune or infer with a deep heatmap regression model

positional arguments:
  {train,tune,infer,locate_peaks}
                        Mode of operation
  config_path      

You can try training multiple models with different starting weights if necessary.

In [13]:
# !python main.py train configs/cystisoma_rhabdoms.yaml -w /home/jake/projects/dhr/logs/paraphronima_rhabdoms/lightning_logs/version_23/checkpoints/epoch=99-step=537600-v1.ckpt -ne 10
# !python main.py train configs/cystisoma_rhabdoms.yaml -w ./logs/paraphronima_rhabdoms_from_pretrained/lightning_logs/version_1/checkpoints/epoch=149-step=900000.ckpt #version_19
# !python main.py train ./configs/cystisoma_rhabdoms.yaml -w ./logs/fiddlercrab_rhabdoms_from_pretrained/lightning_logs/version_1/checkpoints/epoch=123-step=865024.ckpt #version_20 (have not run)
# !python main.py train ./configs/cystisoma_rhabdoms.yaml -w ./logs/cystisoma_rhabdoms/lightning_logs/version_13/checkpoints/epoch=62679-step=4971328.ckpt -ne 10 #version_21 (have not run)

TorchIO version: 0.18.88
("Initiating model using the following config: {'seed': 44, 'lr': "
 "0.0424937961824346, 'num_steps': 1200000, 'weight_decay': "
 "1.52709371682483e-06, 'momentum': 0.510999549987835, 'nesterov': False, "
 "'act': 'ReLU', 'output_activation': 'None', 'softargmax': False, "
 "'num_encoding_blocks': 5, 'out_channels_first_layer': 32, "
 "'double_channels_with_depth': True, 'pooling_type': 'max', "
 "'upsampling_type': 'conv', 'dropout': 0.0175756794552526, "
 "'loss_in_sigma_space': False, 'debug_plots': False, 'mse_with_f1': False, "
 "'visualise_model': False, 'learn_sigma': False, 'optimiser': 'SGD', "
 "'pin_memory': False, 'train_images_dir': "
 "'./dataset/cystisoma_rhabdoms/whole/train_images_10/', 'train_labels_dir': "
 "'./dataset/cystisoma_rhabdoms/whole/train_labels_10/', 'test_images_dir': "
 "'./dataset/cystisoma_rhabdoms/whole/train_images_10/', 'test_labels_dir': "
 "'./dataset/cystisoma_rhabdoms/whole/train_labels_10/', 'image_suffix': "
 "'image

Epoch 151:  95%|▉| 122/128 [01:04<00:03,  1.89it/s, loss=0.000451, v_num=19, tra
Epoch 151:  96%|▉| 123/128 [01:04<00:02,  1.90it/s, loss=0.000451, v_num=19, tra
Epoch 151:  97%|▉| 124/128 [01:04<00:02,  1.92it/s, loss=0.000451, v_num=19, tra
Epoch 151:  98%|▉| 125/128 [01:04<00:01,  1.93it/s, loss=0.000451, v_num=19, tra
Epoch 151:  98%|▉| 126/128 [01:04<00:01,  1.94it/s, loss=0.000451, v_num=19, tra
Epoch 151:  99%|▉| 127/128 [01:04<00:00,  1.95it/s, loss=0.000451, v_num=19, tra
Epoch 151: 100%|█| 128/128 [01:05<00:00,  1.97it/s, loss=0.000451, v_num=19, tra
Epoch 152:  50%|▌| 64/128 [00:24<00:24,  2.61it/s, loss=0.000666, v_num=19, trai
Validation: 0it [00:00, ?it/s]
Validation DataLoader 0:   0%|                           | 0/64 [00:00<?, ?it/s]
Epoch 152:  51%|▌| 65/128 [00:41<00:40,  1.56it/s, loss=0.000666, v_num=19, trai
Epoch 152:  52%|▌| 66/128 [00:41<00:39,  1.58it/s, loss=0.000666, v_num=19, trai
Epoch 152:  52%|▌| 67/128 [00:41<00:38,  1.60it/s, loss=0.000666, v_num=19, tr

Epoch 154:  89%|▉| 114/128 [01:04<00:07,  1.75it/s, loss=0.000452, v_num=19, tra
Epoch 154:  90%|▉| 115/128 [01:05<00:07,  1.77it/s, loss=0.000452, v_num=19, tra
Epoch 154:  91%|▉| 116/128 [01:05<00:06,  1.78it/s, loss=0.000452, v_num=19, tra
Epoch 154:  91%|▉| 117/128 [01:05<00:06,  1.79it/s, loss=0.000452, v_num=19, tra
Epoch 154:  92%|▉| 118/128 [01:05<00:05,  1.81it/s, loss=0.000452, v_num=19, tra
Epoch 154:  93%|▉| 119/128 [01:05<00:04,  1.82it/s, loss=0.000452, v_num=19, tra
Epoch 154:  94%|▉| 120/128 [01:05<00:04,  1.83it/s, loss=0.000452, v_num=19, tra
Epoch 154:  95%|▉| 121/128 [01:05<00:03,  1.85it/s, loss=0.000452, v_num=19, tra
Epoch 154:  95%|▉| 122/128 [01:05<00:03,  1.86it/s, loss=0.000452, v_num=19, tra
Epoch 154:  96%|▉| 123/128 [01:05<00:02,  1.87it/s, loss=0.000452, v_num=19, tra
Epoch 154:  97%|▉| 124/128 [01:05<00:02,  1.89it/s, loss=0.000452, v_num=19, tra
Epoch 154:  98%|▉| 125/128 [01:05<00:01,  1.90it/s, loss=0.000452, v_num=19, tra
Epoch 154:  98%|▉| 126/128 [

Epoch 157:  83%|▊| 106/128 [00:42<00:08,  2.49it/s, loss=0.000247, v_num=19, tra
Epoch 157:  84%|▊| 107/128 [00:42<00:08,  2.51it/s, loss=0.000247, v_num=19, tra
Epoch 157:  84%|▊| 108/128 [00:42<00:07,  2.53it/s, loss=0.000247, v_num=19, tra
Epoch 157:  85%|▊| 109/128 [00:42<00:07,  2.55it/s, loss=0.000247, v_num=19, tra
Epoch 157:  86%|▊| 110/128 [00:42<00:07,  2.57it/s, loss=0.000247, v_num=19, tra
Epoch 157:  87%|▊| 111/128 [00:42<00:06,  2.58it/s, loss=0.000247, v_num=19, tra
Epoch 157:  88%|▉| 112/128 [00:43<00:06,  2.60it/s, loss=0.000247, v_num=19, tra
Epoch 157:  88%|▉| 113/128 [00:43<00:05,  2.62it/s, loss=0.000247, v_num=19, tra
Epoch 157:  89%|▉| 114/128 [00:43<00:05,  2.64it/s, loss=0.000247, v_num=19, tra
Epoch 157:  90%|▉| 115/128 [00:43<00:04,  2.66it/s, loss=0.000247, v_num=19, tra
Epoch 157:  91%|▉| 116/128 [00:43<00:04,  2.68it/s, loss=0.000247, v_num=19, tra
Epoch 157:  91%|▉| 117/128 [00:43<00:04,  2.69it/s, loss=0.000247, v_num=19, tra
Epoch 157:  92%|▉| 118/128 [

Epoch 160:  77%|▊| 98/128 [01:04<00:19,  1.52it/s, loss=0.000363, v_num=19, trai
Epoch 160:  77%|▊| 99/128 [01:04<00:18,  1.54it/s, loss=0.000363, v_num=19, trai
Epoch 160:  78%|▊| 100/128 [01:04<00:18,  1.55it/s, loss=0.000363, v_num=19, tra
Epoch 160:  79%|▊| 101/128 [01:04<00:17,  1.56it/s, loss=0.000363, v_num=19, tra
Epoch 160:  80%|▊| 102/128 [01:04<00:16,  1.58it/s, loss=0.000363, v_num=19, tra
Epoch 160:  80%|▊| 103/128 [01:04<00:15,  1.59it/s, loss=0.000363, v_num=19, tra
Epoch 160:  81%|▊| 104/128 [01:04<00:14,  1.60it/s, loss=0.000363, v_num=19, tra
Epoch 160:  82%|▊| 105/128 [01:04<00:14,  1.62it/s, loss=0.000363, v_num=19, tra
Epoch 160:  83%|▊| 106/128 [01:05<00:13,  1.63it/s, loss=0.000363, v_num=19, tra
Epoch 160:  84%|▊| 107/128 [01:05<00:12,  1.64it/s, loss=0.000363, v_num=19, tra
Epoch 160:  84%|▊| 108/128 [01:05<00:12,  1.66it/s, loss=0.000363, v_num=19, tra
Epoch 160:  85%|▊| 109/128 [01:05<00:11,  1.67it/s, loss=0.000363, v_num=19, tra
Epoch 160:  86%|▊| 110/128 [

...

Epoch 542:  82%|▊| 105/128 [00:43<00:09,  2.42it/s, loss=0.000128, v_num=19, tra
Epoch 542:  83%|▊| 106/128 [00:43<00:09,  2.44it/s, loss=0.000128, v_num=19, tra
Epoch 542:  84%|▊| 107/128 [00:43<00:08,  2.46it/s, loss=0.000128, v_num=19, tra
Epoch 542:  84%|▊| 108/128 [00:43<00:08,  2.48it/s, loss=0.000128, v_num=19, tra
Epoch 542:  85%|▊| 109/128 [00:43<00:07,  2.50it/s, loss=0.000128, v_num=19, tra
Epoch 542:  86%|▊| 110/128 [00:43<00:07,  2.51it/s, loss=0.000128, v_num=19, tra
Epoch 542:  87%|▊| 111/128 [00:43<00:06,  2.53it/s, loss=0.000128, v_num=19, tra
Epoch 542:  88%|▉| 112/128 [00:43<00:06,  2.55it/s, loss=0.000128, v_num=19, tra
Epoch 542:  88%|▉| 113/128 [00:43<00:05,  2.57it/s, loss=0.000128, v_num=19, tra
Epoch 542:  89%|▉| 114/128 [00:44<00:05,  2.59it/s, loss=0.000128, v_num=19, tra
Epoch 542:  90%|▉| 115/128 [00:44<00:04,  2.60it/s, loss=0.000128, v_num=19, tra
Epoch 542:  91%|▉| 116/128 [00:44<00:04,  2.62it/s, loss=0.000128, v_num=19, tra
Epoch 542:  91%|▉| 117/128 [

Epoch 545:  76%|▊| 97/128 [01:03<00:20,  1.52it/s, loss=0.000125, v_num=19, trai
Epoch 545:  77%|▊| 98/128 [01:03<00:19,  1.54it/s, loss=0.000125, v_num=19, trai
Epoch 545:  77%|▊| 99/128 [01:03<00:18,  1.55it/s, loss=0.000125, v_num=19, trai
Epoch 545:  78%|▊| 100/128 [01:03<00:17,  1.57it/s, loss=0.000125, v_num=19, tra
Epoch 545:  79%|▊| 101/128 [01:03<00:17,  1.58it/s, loss=0.000125, v_num=19, tra
Epoch 545:  80%|▊| 102/128 [01:03<00:16,  1.59it/s, loss=0.000125, v_num=19, tra
Epoch 545:  80%|▊| 103/128 [01:04<00:15,  1.61it/s, loss=0.000125, v_num=19, tra
Epoch 545:  81%|▊| 104/128 [01:04<00:14,  1.62it/s, loss=0.000125, v_num=19, tra
Epoch 545:  82%|▊| 105/128 [01:04<00:14,  1.63it/s, loss=0.000125, v_num=19, tra
Epoch 545:  83%|▊| 106/128 [01:04<00:13,  1.65it/s, loss=0.000125, v_num=19, tra
Epoch 545:  84%|▊| 107/128 [01:04<00:12,  1.66it/s, loss=0.000125, v_num=19, tra
Epoch 545:  84%|▊| 108/128 [01:04<00:11,  1.68it/s, loss=0.000125, v_num=19, tra
Epoch 545:  85%|▊| 109/128 [

Epoch 548:  70%|▋| 89/128 [01:02<00:27,  1.42it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  70%|▋| 90/128 [01:02<00:26,  1.43it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  71%|▋| 91/128 [01:03<00:25,  1.44it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  72%|▋| 92/128 [01:03<00:24,  1.46it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  73%|▋| 93/128 [01:03<00:23,  1.47it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  73%|▋| 94/128 [01:03<00:22,  1.49it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  74%|▋| 95/128 [01:03<00:22,  1.50it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  75%|▊| 96/128 [01:03<00:21,  1.51it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  76%|▊| 97/128 [01:03<00:20,  1.53it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  77%|▊| 98/128 [01:03<00:19,  1.54it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  77%|▊| 99/128 [01:03<00:18,  1.56it/s, loss=7.88e-05, v_num=19, trai
Epoch 548:  78%|▊| 100/128 [01:03<00:17,  1.57it/s, loss=7.88e-05, v_num=19, tra
Epoch 548:  79%|▊| 101/128 [

Epoch 551:  63%|▋| 81/128 [00:59<00:34,  1.37it/s, loss=0.000228, v_num=19, trai
Epoch 551:  64%|▋| 82/128 [00:59<00:33,  1.39it/s, loss=0.000228, v_num=19, trai
Epoch 551:  65%|▋| 83/128 [00:59<00:32,  1.40it/s, loss=0.000228, v_num=19, trai
Epoch 551:  66%|▋| 84/128 [00:59<00:31,  1.42it/s, loss=0.000228, v_num=19, trai
Epoch 551:  66%|▋| 85/128 [00:59<00:30,  1.43it/s, loss=0.000228, v_num=19, trai
Epoch 551:  67%|▋| 86/128 [00:59<00:29,  1.45it/s, loss=0.000228, v_num=19, trai
Epoch 551:  68%|▋| 87/128 [00:59<00:28,  1.46it/s, loss=0.000228, v_num=19, trai
Epoch 551:  69%|▋| 88/128 [00:59<00:27,  1.48it/s, loss=0.000228, v_num=19, trai
Epoch 551:  70%|▋| 89/128 [00:59<00:26,  1.49it/s, loss=0.000228, v_num=19, trai
Epoch 551:  70%|▋| 90/128 [00:59<00:25,  1.51it/s, loss=0.000228, v_num=19, trai
Epoch 551:  71%|▋| 91/128 [00:59<00:24,  1.52it/s, loss=0.000228, v_num=19, trai
Epoch 551:  72%|▋| 92/128 [00:59<00:23,  1.54it/s, loss=0.000228, v_num=19, trai
Epoch 551:  73%|▋| 93/128 [0

Epoch 554:  57%|▌| 73/128 [00:58<00:43,  1.26it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  58%|▌| 74/128 [00:58<00:42,  1.27it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  59%|▌| 75/128 [00:58<00:41,  1.29it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  59%|▌| 76/128 [00:58<00:39,  1.30it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  60%|▌| 77/128 [00:58<00:38,  1.32it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  61%|▌| 78/128 [00:58<00:37,  1.33it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  62%|▌| 79/128 [00:58<00:36,  1.35it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  62%|▋| 80/128 [00:58<00:35,  1.37it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  63%|▋| 81/128 [00:58<00:34,  1.38it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  64%|▋| 82/128 [00:58<00:32,  1.40it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  65%|▋| 83/128 [00:58<00:31,  1.41it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  66%|▋| 84/128 [00:58<00:30,  1.43it/s, loss=9.71e-05, v_num=19, trai
Epoch 554:  66%|▋| 85/128 [0

## Inference

First open your heatmap in napari. Use the point selector to select some neighbouring rhabdoms and create a csv file of these selected points. You will use this to make your resampling ratio.

In [ ]:
# load in the nifti file with torchio
# 2nd scan
image_path = '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii'

image = tio.ScalarImage(image_path)


In [ ]:
image

In [ ]:
# view file with napari
import napari


viewer = napari.view_image(image.numpy(), name='image')


In napari, label a few of the features (that are next to each other) to estimate the resample ratio, then save it as a csv file and load it in the next step


In [2]:
import pandas as pd

#Read in your csv and assign it to the variable RR
# 2nd scan
RR = pd.read_csv('/home/jake/projects/dhr/Cystisoma_Hawaii_FEG20190213_rhabdoms_estimating_resampling_ratio.csv')

RR

index  axis-0  axis-1      axis-2      axis-3
0     0.0     0.0   121.0  935.369470  943.075413
1     1.0     0.0   121.0  958.530798  938.844017
2     2.0     0.0   121.0  974.120153  958.442064
3     3.0     0.0   121.0  950.958825  966.682151
4     4.0     0.0   121.0  919.780115  926.817943
5     5.0     0.0   121.0  905.972400  935.726146
6     6.0     0.0   121.0  914.212488  957.105833
7     7.0     0.0   121.0  904.835604  908.432323
8     8.0     0.0   121.0  887.687313  916.672411
9     9.0     0.0   121.0  938.909480  921.571923
10   10.0     0.0   121.0  981.000739  934.711522
11   11.0     0.0   121.0  997.480915  949.632762
12   12.0     0.0   121.0  993.026813  979.029832

In [3]:
from scipy.spatial import distance_matrix

coordinates = RR[['axis-1', 'axis-2', 'axis-3']].values
dist_matrix = distance_matrix(coordinates, coordinates) #Create a distance matrix between points

In [4]:
import numpy as np
np.fill_diagonal(dist_matrix, np.inf)

# Find the nearest neighbor distance for each point
nearest_distances = np.min(dist_matrix, axis=1)

# Add the nearest distances to the dataframe
RR['nearest_distance'] = nearest_distances
RR

index  axis-0  axis-1      axis-2      axis-3  nearest_distance
0     0.0     0.0   121.0  935.369470  943.075413         21.792930
1     1.0     0.0   121.0  958.530798  938.844017         22.846789
2     2.0     0.0   121.0  974.120153  958.442064         24.583453
3     3.0     0.0   121.0  950.958825  966.682151         24.583453
4     4.0     0.0   121.0  919.780115  926.817943         16.431953
5     5.0     0.0   121.0  905.972400  935.726146         16.431953
6     6.0     0.0   121.0  914.212488  957.105833         22.912662
7     7.0     0.0   121.0  904.835604  908.432323         19.025323
8     8.0     0.0   121.0  887.687313  916.672411         19.025323
9     9.0     0.0   121.0  938.909480  921.571923         19.835659
10   10.0     0.0   121.0  981.000739  934.711522         22.231500
11   11.0     0.0   121.0  997.480915  949.632762         22.231500
12   12.0     0.0   121.0  993.026813  979.029832         27.952066

In [5]:
mean_nearest_distance = RR['nearest_distance'].mean()
mean_nearest_distance
resample_ratio = mean_nearest_distance/10
resample_ratio #Print your RR; use this to make your inference 

2.152958176307709

Now you can make your inference. Make sure you have the correct yaml, scan and model path, and have inserted your new resampling ratio. This will produce 3 files: 2 csv files (one resampled and the other not) with the predicted points, and a nifty file with your heatmap.

In [10]:
# Me trying different inferences on version_17 
# Note:(-w for version_17 was cystisoma rhabdoms version_13 and starting sigma was only 2)
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_17/ -rr 2.152958176307709 -nx 1 -ny 1 -nz 1 -ipmv 0.2 -at 0.2
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_17/ -rr 2.152958176307709 -nx 1 -ny 1 -nz 1 -ipmv 0.3 -at 0.3
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_17/ -rr 2.152958176307709 -nx 1 -ny 1 -nz 1 -ipmv 0.4 -at 0.4
!python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_17/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.2

TorchIO version: 0.18.88
Running setup!
Found 1 labelled images with labels in ./dataset/cystisoma_rhabdoms/whole/train_images_10/ and ./dataset/cystisoma_rhabdoms/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/venv/lib/python3.10/site-packages/torch/utils/data/dataset.py:348: UserWarning: Length of split at index 1 is 0. This might result in an empty dataset.
  warnings.warn(f"Length of split at index {i} is 0. "
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 1 labelled images with labels in ./dataset/cystisoma_rhabdoms/whole/train_images_10/ and ./dataset/cystisoma_rhabdoms/whole/train_labels_10/ for analysis
Training:   1
Validation:  1
Test:       1
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_

TorchIO version: 0.18.88
Running setup!
Found 1 labelled images with labels in ./dataset/cystisoma_rhabdoms/whole/train_images_10/ and ./dataset/cystisoma_rhabdoms/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/venv/lib/python3.10/site-packages/torch/utils/data/dataset.py:348: UserWarning: Length of split at index 1 is 0. This might result in an empty dataset.
  warnings.warn(f"Length of split at index {i} is 0. "
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 1 labelled images with labels in ./dataset/cystisoma_rhabdoms/whole/train_images_10/ and ./dataset/cystisoma_rhabdoms/whole/train_labels_10/ for analysis
Training:   1
Validation:  1
Test:       1
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_

  4%|█▋                                         | 5/126 [00:02<01:02,  1.93it/s]


  5%|██                                         | 6/126 [00:03<01:01,  1.95it/s]


  6%|██▍                                        | 7/126 [00:03<01:00,  1.97it/s]


  6%|██▋                                        | 8/126 [00:04<00:59,  1.98it/s]


  7%|███                                        | 9/126 [00:04<00:58,  1.99it/s]


  8%|███▎                                      | 10/126 [00:05<00:57,  2.00it/s]


  9%|███▋                                      | 11/126 [00:05<00:57,  2.00it/s]


 10%|████                                      | 12/126 [00:06<00:57,  1.99it/s]


 10%|████▎                                     | 13/126 [00:06<00:56,  2.00it/s]


 11%|████▋                                     | 14/126 [00:07<00:56,  1.97it/s]


 12%|█████                                     | 15/126 [00:07<00:56,  1.98it/s]


 13%|█████▎                                    | 16/126 [00:08<00:55,  1.98it/s]


 13%

 40%|█████████████████                         | 51/126 [00:25<00:37,  1.99it/s]


 41%|█████████████████▎                        | 52/126 [00:26<00:37,  1.99it/s]


 42%|█████████████████▋                        | 53/126 [00:26<00:36,  1.99it/s]


 43%|██████████████████                        | 54/126 [00:27<00:36,  1.99it/s]


 44%|██████████████████▎                       | 55/126 [00:27<00:35,  2.00it/s]


 44%|██████████████████▋                       | 56/126 [00:28<00:35,  2.00it/s]


 45%|███████████████████                       | 57/126 [00:28<00:35,  1.96it/s]


 46%|███████████████████▎                      | 58/126 [00:29<00:35,  1.94it/s]


 47%|███████████████████▋                      | 59/126 [00:29<00:34,  1.92it/s]


 48%|████████████████████                      | 60/126 [00:30<00:33,  1.95it/s]


 48%|████████████████████▎                     | 61/126 [00:30<00:33,  1.97it/s]


 49%|████████████████████▋                     | 62/126 [00:31<00:32,  1.98it/s]


 50%

  5%|██                                         | 6/126 [00:03<01:00,  1.97it/s]


  6%|██▍                                        | 7/126 [00:03<00:59,  1.99it/s]


  6%|██▋                                        | 8/126 [00:04<00:59,  1.99it/s]


  7%|███                                        | 9/126 [00:04<00:59,  1.97it/s]


  8%|███▎                                      | 10/126 [00:05<00:59,  1.96it/s]


  9%|███▋                                      | 11/126 [00:05<00:59,  1.92it/s]


 10%|████                                      | 12/126 [00:06<00:59,  1.91it/s]


 10%|████▎                                     | 13/126 [00:06<00:59,  1.90it/s]


 11%|████▋                                     | 14/126 [00:07<00:58,  1.91it/s]


 12%|█████                                     | 15/126 [00:07<00:57,  1.93it/s]


 13%|█████▎                                    | 16/126 [00:08<00:56,  1.95it/s]


 13%|█████▋                                    | 17/126 [00:08<00:55,  1.97it/s]


 14%

 41%|█████████████████▎                        | 52/126 [00:26<00:37,  1.99it/s]


 42%|█████████████████▋                        | 53/126 [00:26<00:37,  1.96it/s]


 43%|██████████████████                        | 54/126 [00:27<00:36,  1.96it/s]


 44%|██████████████████▎                       | 55/126 [00:27<00:36,  1.96it/s]


 44%|██████████████████▋                       | 56/126 [00:28<00:35,  1.96it/s]


 45%|███████████████████                       | 57/126 [00:28<00:35,  1.97it/s]


 46%|███████████████████▎                      | 58/126 [00:29<00:34,  1.98it/s]


 47%|███████████████████▋                      | 59/126 [00:29<00:33,  1.99it/s]


 48%|████████████████████                      | 60/126 [00:30<00:33,  2.00it/s]


 48%|████████████████████▎                     | 61/126 [00:30<00:32,  2.00it/s]


 49%|████████████████████▋                     | 62/126 [00:31<00:31,  2.00it/s]


 50%|█████████████████████                     | 63/126 [00:31<00:31,  1.98it/s]


 51%

...

 48%|████████████████████▎                     | 61/126 [00:30<00:32,  2.01it/s]


 49%|████████████████████▋                     | 62/126 [00:30<00:31,  2.01it/s]


 50%|█████████████████████                     | 63/126 [00:31<00:31,  2.01it/s]


 51%|█████████████████████▎                    | 64/126 [00:31<00:30,  2.01it/s]


 52%|█████████████████████▋                    | 65/126 [00:32<00:30,  2.00it/s]


 52%|██████████████████████                    | 66/126 [00:32<00:29,  2.01it/s]


 53%|██████████████████████▎                   | 67/126 [00:33<00:29,  2.01it/s]


 54%|██████████████████████▋                   | 68/126 [00:33<00:28,  2.01it/s]


 55%|███████████████████████                   | 69/126 [00:34<00:28,  2.01it/s]


 56%|███████████████████████▎                  | 70/126 [00:34<00:27,  2.01it/s]


 56%|███████████████████████▋                  | 71/126 [00:35<00:27,  2.01it/s]


 57%|████████████████████████                  | 72/126 [00:35<00:26,  2.01it/s]


 58%

 83%|█████████████████████████████████▊       | 104/126 [00:52<00:10,  2.01it/s]


 83%|██████████████████████████████████▏      | 105/126 [00:52<00:10,  2.01it/s]


 84%|██████████████████████████████████▍      | 106/126 [00:53<00:09,  2.01it/s]


 85%|██████████████████████████████████▊      | 107/126 [00:53<00:09,  2.00it/s]


 86%|███████████████████████████████████▏     | 108/126 [00:54<00:08,  2.00it/s]


 87%|███████████████████████████████████▍     | 109/126 [00:54<00:08,  1.98it/s]


 87%|███████████████████████████████████▊     | 110/126 [00:55<00:08,  1.99it/s]


 88%|████████████████████████████████████     | 111/126 [00:55<00:07,  1.99it/s]


 89%|████████████████████████████████████▍    | 112/126 [00:56<00:07,  1.99it/s]


 90%|████████████████████████████████████▊    | 113/126 [00:56<00:06,  2.00it/s]


 90%|█████████████████████████████████████    | 114/126 [00:57<00:06,  2.00it/s]


 91%|█████████████████████████████████████▍   | 115/126 [00:57<00:05,  2.00it/s]


 92%

 14%|██████                                    | 18/126 [00:09<00:53,  2.02it/s]


 15%|██████▎                                   | 19/126 [00:09<00:53,  2.02it/s]


 16%|██████▋                                   | 20/126 [00:10<00:52,  2.01it/s]


 17%|███████                                   | 21/126 [00:10<00:52,  2.01it/s]


 17%|███████▎                                  | 22/126 [00:11<00:51,  2.01it/s]


 18%|███████▋                                  | 23/126 [00:11<00:51,  2.01it/s]


 19%|████████                                  | 24/126 [00:12<00:50,  2.01it/s]


 20%|████████▎                                 | 25/126 [00:12<00:50,  2.01it/s]


 21%|████████▋                                 | 26/126 [00:13<00:49,  2.01it/s]


 21%|█████████                                 | 27/126 [00:13<00:49,  2.01it/s]


 22%|█████████▎                                | 28/126 [00:14<00:48,  2.01it/s]


 23%|█████████▋                                | 29/126 [00:14<00:48,  2.01it/s]


 24%

 48%|████████████████████▎                     | 61/126 [00:30<00:32,  2.01it/s]


 49%|████████████████████▋                     | 62/126 [00:30<00:31,  2.00it/s]


 50%|█████████████████████                     | 63/126 [00:31<00:31,  2.01it/s]


 51%|█████████████████████▎                    | 64/126 [00:31<00:30,  2.01it/s]


 52%|█████████████████████▋                    | 65/126 [00:32<00:30,  2.01it/s]


 52%|██████████████████████                    | 66/126 [00:32<00:29,  2.01it/s]


 53%|██████████████████████▎                   | 67/126 [00:33<00:29,  2.01it/s]


 54%|██████████████████████▋                   | 68/126 [00:33<00:28,  2.01it/s]


 55%|███████████████████████                   | 69/126 [00:34<00:28,  2.01it/s]


 56%|███████████████████████▎                  | 70/126 [00:34<00:27,  2.01it/s]


 56%|███████████████████████▋                  | 71/126 [00:35<00:27,  2.01it/s]


 57%|████████████████████████                  | 72/126 [00:35<00:26,  2.01it/s]


 58%

 85%|██████████████████████████████████▊      | 107/126 [00:53<00:09,  2.00it/s]


 86%|███████████████████████████████████▏     | 108/126 [00:53<00:08,  2.00it/s]


 87%|███████████████████████████████████▍     | 109/126 [00:54<00:08,  2.00it/s]


 87%|███████████████████████████████████▊     | 110/126 [00:54<00:07,  2.00it/s]


 88%|████████████████████████████████████     | 111/126 [00:55<00:07,  2.01it/s]


 89%|████████████████████████████████████▍    | 112/126 [00:55<00:06,  2.00it/s]


 90%|████████████████████████████████████▊    | 113/126 [00:56<00:06,  2.00it/s]


 90%|█████████████████████████████████████    | 114/126 [00:56<00:05,  2.01it/s]


 91%|█████████████████████████████████████▍   | 115/126 [00:57<00:05,  2.00it/s]


 92%|█████████████████████████████████████▋   | 116/126 [00:57<00:04,  2.00it/s]


 93%|██████████████████████████████████████   | 117/126 [00:58<00:04,  2.00it/s]


 94%|██████████████████████████████████████▍  | 118/126 [00:58<00:04,  2.00it/s]


 94%

In [7]:
# Me trying different inferences for version_19 
# (Note:-w for version_19 was paraphronima_rhabdoms_from_pretrainied version_1 and starting sigma was changed to 4)
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 1 -ny 1 -nz 1 -ipmv 0.5 -at 0.5
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 1 -ny 1 -nz 1 -ipmv 0.2 -at 0.2
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 1 -ny 1 -nz 1 -ipmv 0.3 -at 0.3
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 2 -ny 2 -nz 2 -ipmv 0.5 -at 0.5
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.4
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.4
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.4
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.45 -at 0.4

# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.5
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.3 -at 0.5
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.2 -at 0.5
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.5
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.5
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.3
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.2
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.4 -at 0.1
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.15
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.25
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.35
# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.45

# !python main.py infer configs/cystisoma_rhabdoms.yaml -v '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii' -m ./logs/cystisoma_rhabdoms/lightning_logs/version_19/ -rr 2.152958176307709 -nx 3 -ny 3 -nz 3 -ipmv 0.45 -at 0.5





TorchIO version: 0.18.88
Running setup!
Found 1 labelled images with labels in ./dataset/cystisoma_rhabdoms/whole/train_images_10/ and ./dataset/cystisoma_rhabdoms/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/venv/lib/python3.10/site-packages/torch/utils/data/dataset.py:348: UserWarning: Length of split at index 1 is 0. This might result in an empty dataset.
  warnings.warn(f"Length of split at index {i} is 0. "
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 1 labelled images with labels in ./dataset/cystisoma_rhabdoms/whole/train_images_10/ and ./dataset/cystisoma_rhabdoms/whole/train_labels_10/ for analysis
Training:   1
Validation:  1
Test:       1
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_

You can then view your inference in napari.

In [8]:
import napari
import numpy as np
import torchio as tio


image_path = '/media/jake/2tb_ssd/mctv_data/Cystisoma_Hawaii_FEG20190213_01_head/FEG20190213_010.nii'
image = tio.ScalarImage(image_path)

# heatmap_path = '/media/jake/Removable backup/Jake/projects/dhr/output/FEG20190213_010.logs_cystisoma_rhabdoms_lightning_logs_version_17_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction.nii'
heatmap_path = '/home/jake/projects/dhr/output/FEG20190213_010.logs_cystisoma_rhabdoms_lightning_logs_version_19_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction.nii'

#Make sure to use resampled space csv here.
# y_hat_path = '/media/jake/Removable backup/Jake/projects/dhr/output/FEG20190213_010.logs_cystisoma_rhabdoms_lightning_logs_version_17_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction_peak_min_val_0_5_method_center_of_mass.resampled_space_peaks.csv'
y_hat_path = '/home/jake/projects/dhr/output/FEG20190213_010.logs_cystisoma_rhabdoms_lightning_logs_version_19_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction_peak_min_val_0_45_method_center_of_mass.resampled_space_peaks.csv'

heatmap = tio.ScalarImage(heatmap_path)


viewer = napari.view_image(heatmap.numpy(), name='heatmap', contrast_limits=[0, 1])
# viewer.add _image(image.numpy(), name='image') #If you want to view your scan also (not necessary)

# load the coordinates to analyse
def load_coordinates(path, flip_axes=False, mct_path=None):
    locations = np.loadtxt(
        path,
        delimiter=',',
        ndmin=2,
        dtype=np.float64
    )
    if not flip_axes: 
        return locations.tolist()

    if not mct_path:
        raise Exception('You must specify `mct_path` if you need to flip_axes')

    mct = tio.ScalarImage(mct_path)
    locations[:,0] = mct.shape[1] - locations[:,0]
    locations[:,1] = mct.shape[2] - locations[:,1]

    return locations.tolist()


y_hat = load_coordinates(y_hat_path)


viewer.add_points(y_hat)

<Points layer 'Points' at 0x7f5442b41940>

# Primno corneas

## Generate dataset

Convert your mat file into a csv file for corneas labels for each already labelled scan (save to raw_labels folder:'/home/jake/projects/dhr/dataset/raw_labels'). Create a csv called primno_corneas.csv (for structure of this csv see dhr: https://github.com/jakemanger/dhr)(save to data_source_specifiers folder: '/home/jake/projects/dhr/data_source_specifiers'). Insert the raw labels paths and image paths into this csv. 

In [26]:
!python mctv_to_csv.py -h

# This method is not appropriate for Primno (currently) and does not include all 4 eyes, see steps below to convert mat to csv
# !python mctv_to_csv.py '/home/jake/projects/dhr/data_source_specifiers/primno_corneas.csv'

usage: mctv_to_csv.py [-h] data_source_specifier_path

Converts .mat files from the mctv program (an internal tool in JanHemmi's lab
at UWA) to .csv.

positional arguments:
  data_source_specifier_path
                        The path to your .csv file that specifies where your
                        images and labels are and whether it should be used
                        for training or testing. This .csv file should have
                        the following columns: 1. mctv_label_file_path (matlab
                        files with corneas and rhabdoms generated by mctv)
                        Example: data_source_specifiers/fiddler.csv or
                        data_source_specifiers/paraphronima.csv

options:
  -h, --help            show this help message and exit


Use the next few blocks to explore your mat file. You should only need this once.

In [66]:
# Use this block of code to examine dictionary keys in your mat file
import h5py

file_path = '/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_356/Primno_abyssalis_356_eye.mat'
mat = h5py.File(file_path, 'r')

# List all top-level keys (variable names)
print("Keys (variable names) in the .mat file:")
keys = list(mat.keys())
print(keys)

# Use this block of code to view contents in save_dat
if isinstance(mat['save_dat'], h5py.Group):
    print("\n'save_dat' is a group. Listing its contents:")
    save_dat_group = mat['save_dat']
    group_keys = list(save_dat_group.keys())
    print(group_keys)

    for key in group_keys:
        item = save_dat_group[key]
        if isinstance(item, h5py.Dataset):
            # If it's a dataset, print its details
            print(f"\n'{key}' is a dataset.")
            print(f"Data type of {key}: {item.dtype}")
            print(f"Shape of {key}: {item.shape}")

            # Convert the dataset to a NumPy array if needed
            data_array = item[:]
            print(f"Data from {key}:\n", data_array)
        elif isinstance(item, h5py.Group):
            # If it's a group, print that it's a group
            print(f"\n'{key}' is a group.")
        else:
            print(f"'{key}' is of unknown type.")



Keys (variable names) in the .mat file:
['#refs#', 'save_dat']

'save_dat' is a group. Listing its contents:
['ana', 'auto', 'autosave', 'cur', 'data', 'eye_shape_file', 'figh', 'figh_ana', 'figh_fana', 'gd', 'ref_shape_file', 'retina_shape_file', 'rmfields', 'rotation_size_limit', 'rotation_size_min', 'savename', 'stack']

'ana' is a group.

'auto' is a group.

'autosave' is a group.

'cur' is a group.

'data' is a group.

'eye_shape_file' is a dataset.
Data type of eye_shape_file: uint64
Shape of eye_shape_file: (2,)
Data from eye_shape_file:
 [0 0]

'figh' is a dataset.
Data type of figh: float64
Shape of figh: (1, 1)
Data from figh:
 [[121.]]

'figh_ana' is a dataset.
Data type of figh_ana: float64
Shape of figh_ana: (1, 1)
Data from figh_ana:
 [[777.]]

'figh_fana' is a dataset.
Data type of figh_fana: float64
Shape of figh_fana: (1, 1)
Data from figh_fana:
 [[888.]]

'gd' is a group.

'ref_shape_file' is a dataset.
Data type of ref_shape_file: uint64
Shape of ref_shape_file: (2,)

In [69]:
with h5py.File('/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_356/Primno_abyssalis_356_eye.mat', 'r') as mat:
    save_dat_group = mat['save_dat']
    
    def explore_group(group):
        for name, item in group.items():
            if isinstance(item, h5py.Group):
                print(f"Group: {name}")
                explore_group(item) 
            elif isinstance(item, h5py.Dataset):
                print(f"Dataset: {name}, Shape: {item.shape}, Data Type: {item.dtype}")

    # Start exploring from save_dat_group
    explore_group(save_dat_group)



Group: ana
Group: para
Dataset: allow_splitting_rows_by_distance, Shape: (1, 1), Data Type: float64
Dataset: distance_for_pointtext, Shape: (1, 1), Data Type: float64
Dataset: include_non_empty, Shape: (1, 1), Data Type: float64
Dataset: main_marker_size, Shape: (1, 1), Data Type: float64
Dataset: pt_th, Shape: (1, 1), Data Type: float64
Dataset: row_th, Shape: (1, 1), Data Type: float64
Dataset: spline_stiff, Shape: (1, 1), Data Type: float64
Dataset: spline_stiff_smooth, Shape: (1, 1), Data Type: float64
Dataset: spline_stiff_soft_mult, Shape: (1, 1), Data Type: float64
Dataset: spline_stiff_z_mult, Shape: (1, 1), Data Type: float64
Dataset: text_size, Shape: (1, 1), Data Type: float64
Group: auto
Dataset: convsize, Shape: (1, 1), Data Type: float64
Dataset: dotsize, Shape: (1, 1), Data Type: float64
Dataset: dotsoze, Shape: (1, 1), Data Type: float64
Dataset: ltarget, Shape: (1, 1), Data Type: float64
Dataset: replacedist, Shape: (1, 1), Data Type: float64
Dataset: searchsize, Shape

In [73]:
# Use this block of code to explore the structure of groups (i.e. in this case you want to use this code to find the names of group to be used in the next block)
with h5py.File('/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_356/Primno_abyssalis_356_eye.mat', 'r') as file:
    def print_structure(name, obj):
        print(f"{name}: {obj}")
    
    file.visititems(print_structure) 

#refs#: <HDF5 group "/#refs#" (31 members)>
#refs#/A: <HDF5 dataset "A": shape (8, 1), type "<u2">
#refs#/B: <HDF5 dataset "B": shape (7, 1), type "<u2">
#refs#/C: <HDF5 dataset "C": shape (2, 1), type "<u2">
#refs#/D: <HDF5 dataset "D": shape (12, 1), type "<u2">
#refs#/E: <HDF5 dataset "E": shape (4, 1), type "<u2">
#refs#/a: <HDF5 dataset "a": shape (2,), type "<u8">
#refs#/b: <HDF5 dataset "b": shape (1, 1), type "<f8">
#refs#/c: <HDF5 dataset "c": shape (1, 1), type "<f8">
#refs#/d: <HDF5 dataset "d": shape (1, 1), type "<f8">
#refs#/e: <HDF5 dataset "e": shape (1, 1), type "<f8">
#refs#/f: <HDF5 dataset "f": shape (1, 1), type "<u2">
#refs#/g: <HDF5 dataset "g": shape (1, 1), type "<u2">
#refs#/h: <HDF5 dataset "h": shape (1, 1), type "<u2">
#refs#/i: <HDF5 dataset "i": shape (1, 1), type "<u2">
#refs#/j: <HDF5 dataset "j": shape (1, 1), type "<f8">
#refs#/k: <HDF5 dataset "k": shape (1, 1), type "<f8">
#refs#/l: <HDF5 dataset "l": shape (1, 1), type "<f8">
#refs#/m: <HDF5 datase

In [74]:
import pandas as pd

with h5py.File('/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_356/Primno_abyssalis_356_eye.mat', 'r') as file:
    # Access the marked dataset using the correct path
    marked_data = file['save_dat/data/marked'][:, :1642] 

marked_df = pd.DataFrame(marked_data)

print(marked_df)


         0           1           2           3           4           5     \
0  413.799234  392.224242  418.690916  442.773824  543.599670  549.531006   
1  344.812257  184.796941  205.359985  260.519539   82.198235   76.462900   
2  364.749693  519.553709  486.690526  423.877994  726.151611  758.742294   
3    2.000000    7.000000    6.000000    4.000000  107.000000  104.000000   

         6           7           8           9     ...        1632  \
0  522.830477  515.256420  369.343628  334.354801  ...  566.211948   
1   65.022158   67.909723  115.024315  135.410461  ...  682.205432   
2  782.491818  754.416333  638.070637  625.128479  ...  535.117258   
3  105.000000  108.000000   10.000000   10.000000  ...  105.000000   

         1633        1634        1635        1636        1637        1638  \
0  575.491107  579.392150  583.974905  612.994424  601.249101  488.536180   
1  667.135144  649.146296  636.827338  653.335653  630.081714  727.743198   
2  519.033624  525.633741  541.0

In [ ]:
# Use this block to investigate a specifc row
with h5py.File('/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_356/Primno_abyssalis_356_eye.mat', 'r') as file:
    marked_data = file['save_dat/data/marked'][:]  


marked_df = pd.DataFrame(marked_data)

values = marked_df.iloc[5] # row 5 here contains indexes for corneas and rhabdoms/eye
print(values)


The next blocks of code actually convert your mat file into a csv. Make sure you include your mat path, the path you want to save your csv to (here 'raw_labels'), and include the correct index values (i.e. for corneas or rhabdoms). 

In [95]:
# To convert mat for Primno_abyssalis_FEG221018_357 into corneas raw labels csv
import h5py
import pandas as pd
import os

with h5py.File('/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_357/Primno_abyssalis_357.mat', 'r') as file:
    marked_data = file['save_dat/data/marked'][:]  

marked_df = pd.DataFrame(marked_data)


columns_to_keep = marked_df.iloc[5].isin([0, 2, 4, 6]) # correct indices for corneas
column_indices = marked_df.columns[columns_to_keep]
filtered_df = marked_df.iloc[:3, column_indices]
transposed_df = filtered_df.transpose()

# Specify directory path
save_directory = '/home/jake/projects/dhr/dataset/raw_labels'  
csv_name = 'Primno_abyssalis_FEG221018_357_labels_corneas.csv' # name csv 


csv_path = os.path.join(save_directory, csv_name)


os.makedirs(save_directory, exist_ok=True)


transposed_df.to_csv(csv_path, header=False, index=False)


Values in the sixth row: 0       2.0
1       2.0
2       2.0
3       2.0
4       2.0
       ... 
1649    1.0
1650    1.0
1651    1.0
1652    5.0
1653    3.0
Name: 5, Length: 1654, dtype: float64
CSV saved successfully to: /home/jake/projects/dhr/dataset/raw_labels/Primno_abyssalis_FEG221018_357_labels_corneas.csv


In [17]:
# To convert mat for Primno_abyssalis_FEG221018_356 into corneas raw labels csv
import h5py
import pandas as pd
import os

with h5py.File('/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_356/Primno_abyssalis_356_eye.mat', 'r') as file:
    marked_data = file['save_dat/data/marked'][:]  # Load the entire marked dataset

marked_df = pd.DataFrame(marked_data)


columns_to_keep = marked_df.iloc[5].isin([0, 2, 4, 6]) # correct indices for corneas
column_indices = marked_df.columns[columns_to_keep]
filtered_df = marked_df.iloc[:3, column_indices]
transposed_df = filtered_df.transpose()

# Specify the directory where you want to save the CSV
save_directory = '/home/jake/projects/dhr/dataset/raw_labels'  
csv_name = 'Primno_abyssalis_FEG221018_356_labels_corneas.csv'

csv_path = os.path.join(save_directory, csv_name)

os.makedirs(save_directory, exist_ok=True)

transposed_df.to_csv(csv_path, header=False, index=False)


The next block of code generate your dataset 

In [6]:
# !python generate_dataset.py -h #(dont forget you have generated the corneas datset using rhabdoms csv paths in the corneas data source specifiers csv)
!python generate_dataset.py ./data_source_specifiers/primno_corneas.csv -l corneas -v 10 -cl corneas -cb 16

Processing images with voxel spacing 10
  0%|                                                     | 0/2 [00:00<?, ?it/s]Starting conversion of /media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f356_u0000000/Primno_abyssalis_FEG221018_356.nii
./dataset/primno_corneas/patches/train_images_10/Primno_abyssalis_FEG221018_356 has already been created, so skipping
delete the file if you want to recreate it
Starting conversion of /media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f357_u0000000/Primno_abyssalis_FEG221018_357.nii
./dataset/primno_corneas/patches/train_images_10/Primno_abyssalis_FEG221018_357 has already been created, so skipping
delete the file if you want to recreate it
100%|███████████████████████████████████████████| 2/2 [00:00<00:00, 4086.02it/s]
Processing images with voxel spacing 10
  0%|                                                     | 0/2 [00:00<?, ?it/s]Starting conversion o

## Checking

In [7]:
!python check_data.py ./configs/primno_corneas.yaml

Running setup!
Found 2 labelled images with labels in ./dataset/primno_corneas/whole/train_images_10/ and ./dataset/primno_corneas/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/primno_corneas/whole/train_images_10/ and ./dataset/primno_corneas/whole/train_labels_10/ for analysis
("Initiating model using the following config: {'seed': 44, 'lr': "
 "0.0424937961824346, 'num_steps': 700000, 'weight_decay': "
 "1.52709371682483e-06, 'momentum': 0.510999549987835, 'nesterov': False, "
 "'act': 'ReLU', 'output_activation': 'None', 'softargmax': False, "
 "'num_encoding_blocks': 5, 'out_channels_first_layer': 32, "
 "'double_channels_with_depth': True, 'pooling_type': 'max', "
 "'upsampling_type': 'conv', 'd

## Training

In [10]:
'''version 1'''
# !python main.py train configs/primno_corneas.yaml -w ./logs/cystisoma_corneas/lightning_logs/version_13/checkpoints/epoch=2758-step=696256.ckpt -ne 10
'''version 3'''
!python main.py train configs/primno_corneas.yaml -w ./logs/cystisoma_corneas/lightning_logs/version_14/checkpoints/epoch=3589-step=799360-v1.ckpt -ne 10


TorchIO version: 0.18.88
("Initiating model using the following config: {'seed': 44, 'lr': "
 "0.0424937961824346, 'num_steps': 1100000, 'weight_decay': "
 "1.52709371682483e-06, 'momentum': 0.510999549987835, 'nesterov': False, "
 "'act': 'ReLU', 'output_activation': 'None', 'softargmax': False, "
 "'num_encoding_blocks': 5, 'out_channels_first_layer': 32, "
 "'double_channels_with_depth': True, 'pooling_type': 'max', "
 "'upsampling_type': 'conv', 'dropout': 0.0175756794552526, "
 "'loss_in_sigma_space': False, 'debug_plots': False, 'mse_with_f1': False, "
 "'visualise_model': False, 'learn_sigma': False, 'optimiser': 'SGD', "
 "'pin_memory': False, 'train_images_dir': "
 "'./dataset/primno_corneas/whole/train_images_10/', 'train_labels_dir': "
 "'./dataset/primno_corneas/whole/train_labels_10/', 'test_images_dir': "
 "'./dataset/primno_corneas/whole/train_images_10/', 'test_labels_dir': "
 "'./dataset/primno_corneas/whole/train_labels_10/', 'image_suffix': 'image', "
 "'label_suffix

Epoch 3609:  54%|▌| 137/256 [00:32<00:28,  4.23it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  54%|▌| 138/256 [00:32<00:27,  4.25it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  54%|▌| 139/256 [00:32<00:27,  4.27it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  55%|▌| 140/256 [00:32<00:27,  4.29it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  55%|▌| 141/256 [00:32<00:26,  4.31it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  55%|▌| 142/256 [00:32<00:26,  4.33it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  56%|▌| 143/256 [00:32<00:25,  4.35it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  56%|▌| 144/256 [00:32<00:25,  4.37it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  57%|▌| 145/256 [00:33<00:25,  4.39it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  57%|▌| 146/256 [00:33<00:24,  4.41it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  57%|▌| 147/256 [00:33<00:24,  4.43it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  58%|▌| 148/256 [00:33<00:24,  4.45it/s, loss=0.000618, v_num=3, tra
Epoch 3609:  58%|▌| 149/256 

Epoch 3619:  78%|▊| 200/256 [00:35<00:09,  5.66it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  79%|▊| 201/256 [00:35<00:09,  5.68it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  79%|▊| 202/256 [00:35<00:09,  5.69it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  79%|▊| 203/256 [00:35<00:09,  5.71it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  80%|▊| 204/256 [00:35<00:09,  5.72it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  80%|▊| 205/256 [00:35<00:08,  5.74it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  80%|▊| 206/256 [00:35<00:08,  5.75it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  81%|▊| 207/256 [00:35<00:08,  5.77it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  81%|▊| 208/256 [00:35<00:08,  5.78it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  82%|▊| 209/256 [00:36<00:08,  5.80it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  82%|▊| 210/256 [00:36<00:07,  5.81it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  82%|▊| 211/256 [00:36<00:07,  5.83it/s, loss=0.000539, v_num=3, tra
Epoch 3619:  83%|▊| 212/256 

Epoch 3639:  52%|▌| 132/256 [00:21<00:19,  6.21it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  52%|▌| 133/256 [00:21<00:19,  6.24it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  52%|▌| 134/256 [00:21<00:19,  6.26it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  53%|▌| 135/256 [00:21<00:19,  6.28it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  53%|▌| 136/256 [00:21<00:19,  6.30it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  54%|▌| 137/256 [00:21<00:18,  6.33it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  54%|▌| 138/256 [00:21<00:18,  6.34it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  54%|▌| 139/256 [00:21<00:18,  6.37it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  55%|▌| 140/256 [00:21<00:18,  6.39it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  55%|▌| 141/256 [00:22<00:17,  6.41it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  55%|▌| 142/256 [00:22<00:17,  6.43it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  56%|▌| 143/256 [00:22<00:17,  6.45it/s, loss=0.000716, v_num=3, tra
Epoch 3639:  56%|▌| 144/256 

Epoch 3649:  76%|▊| 195/256 [00:33<00:10,  5.77it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  77%|▊| 196/256 [00:33<00:10,  5.78it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  77%|▊| 197/256 [00:33<00:10,  5.80it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  77%|▊| 198/256 [00:34<00:09,  5.82it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  78%|▊| 199/256 [00:34<00:09,  5.83it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  78%|▊| 200/256 [00:34<00:09,  5.85it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  79%|▊| 201/256 [00:34<00:09,  5.86it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  79%|▊| 202/256 [00:34<00:09,  5.88it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  79%|▊| 203/256 [00:34<00:08,  5.89it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  80%|▊| 204/256 [00:34<00:08,  5.91it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  80%|▊| 205/256 [00:34<00:08,  5.92it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  80%|▊| 206/256 [00:34<00:08,  5.94it/s, loss=0.000518, v_num=3, tra
Epoch 3649:  81%|▊| 207/256 

...

Epoch 3689:  99%|▉| 254/256 [00:40<00:00,  6.30it/s, loss=0.000827, v_num=3, tra
Epoch 3689: 100%|▉| 255/256 [00:40<00:00,  6.32it/s, loss=0.000827, v_num=3, tra
Epoch 3689: 100%|█| 256/256 [00:40<00:00,  6.33it/s, loss=0.000827, v_num=3, tra
Epoch 3699:  50%|▌| 128/256 [00:30<00:30,  4.15it/s, loss=0.000646, v_num=3, tra
Validation: 0it [00:00, ?it/s]
Validation DataLoader 0:   0%|                          | 0/128 [00:00<?, ?it/s]
Epoch 3699:  50%|▌| 129/256 [00:35<00:34,  3.65it/s, loss=0.000646, v_num=3, tra
Epoch 3699:  51%|▌| 130/256 [00:35<00:34,  3.67it/s, loss=0.000646, v_num=3, tra
Epoch 3699:  51%|▌| 131/256 [00:35<00:33,  3.69it/s, loss=0.000646, v_num=3, tra
Epoch 3699:  52%|▌| 132/256 [00:35<00:33,  3.71it/s, loss=0.000646, v_num=3, tra
Epoch 3699:  52%|▌| 133/256 [00:35<00:32,  3.73it/s, loss=0.000646, v_num=3, tra
Epoch 3699:  52%|▌| 134/256 [00:35<00:32,  3.75it/s, loss=0.000646, v_num=3, tra
Epoch 3699:  53%|▌| 135/256 [00:35<00:32,  3.77it/s, loss=0.000646, v_num=3, t

Epoch 3709:  73%|▋| 186/256 [00:34<00:12,  5.46it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  73%|▋| 187/256 [00:34<00:12,  5.48it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  73%|▋| 188/256 [00:34<00:12,  5.49it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  74%|▋| 189/256 [00:34<00:12,  5.51it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  74%|▋| 190/256 [00:34<00:11,  5.53it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  75%|▋| 191/256 [00:34<00:11,  5.54it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  75%|▊| 192/256 [00:34<00:11,  5.56it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  75%|▊| 193/256 [00:34<00:11,  5.58it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  76%|▊| 194/256 [00:34<00:11,  5.59it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  76%|▊| 195/256 [00:34<00:10,  5.61it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  77%|▊| 196/256 [00:34<00:10,  5.62it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  77%|▊| 197/256 [00:34<00:10,  5.64it/s, loss=0.000494, v_num=3, tra
Epoch 3709:  77%|▊| 198/256 

Epoch 3719:  97%|▉| 249/256 [00:30<00:00,  8.13it/s, loss=0.000467, v_num=3, tra
Epoch 3719:  98%|▉| 250/256 [00:30<00:00,  8.14it/s, loss=0.000467, v_num=3, tra
Epoch 3719:  98%|▉| 251/256 [00:30<00:00,  8.16it/s, loss=0.000467, v_num=3, tra
Epoch 3719:  98%|▉| 252/256 [00:30<00:00,  8.17it/s, loss=0.000467, v_num=3, tra
Epoch 3719:  99%|▉| 253/256 [00:30<00:00,  8.18it/s, loss=0.000467, v_num=3, tra
Epoch 3719:  99%|▉| 254/256 [00:31<00:00,  8.19it/s, loss=0.000467, v_num=3, tra
Epoch 3719: 100%|▉| 255/256 [00:31<00:00,  8.20it/s, loss=0.000467, v_num=3, tra
Epoch 3719: 100%|█| 256/256 [00:31<00:00,  8.21it/s, loss=0.000467, v_num=3, tra
Epoch 3729:  50%|▌| 128/256 [00:23<00:23,  5.41it/s, loss=0.000555, v_num=3, tra
Validation: 0it [00:00, ?it/s]
Validation DataLoader 0:   0%|                          | 0/128 [00:00<?, ?it/s]
Epoch 3729:  50%|▌| 129/256 [00:28<00:27,  4.57it/s, loss=0.000555, v_num=3, tra
Epoch 3729:  51%|▌| 130/256 [00:28<00:27,  4.59it/s, loss=0.000555, v_num=3, t

Epoch 3739:  71%|▋| 181/256 [00:23<00:09,  7.65it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  71%|▋| 182/256 [00:23<00:09,  7.67it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  71%|▋| 183/256 [00:23<00:09,  7.69it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  72%|▋| 184/256 [00:23<00:09,  7.70it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  72%|▋| 185/256 [00:23<00:09,  7.72it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  73%|▋| 186/256 [00:24<00:09,  7.74it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  73%|▋| 187/256 [00:24<00:08,  7.76it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  73%|▋| 188/256 [00:24<00:08,  7.77it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  74%|▋| 189/256 [00:24<00:08,  7.79it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  74%|▋| 190/256 [00:24<00:08,  7.81it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  75%|▋| 191/256 [00:24<00:08,  7.82it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  75%|▊| 192/256 [00:24<00:08,  7.84it/s, loss=0.000336, v_num=3, tra
Epoch 3739:  75%|▊| 193/256 

Epoch 3749:  95%|▉| 244/256 [00:37<00:01,  6.58it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  96%|▉| 245/256 [00:37<00:01,  6.59it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  96%|▉| 246/256 [00:37<00:01,  6.61it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  96%|▉| 247/256 [00:37<00:01,  6.62it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  97%|▉| 248/256 [00:37<00:01,  6.63it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  97%|▉| 249/256 [00:37<00:01,  6.65it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  98%|▉| 250/256 [00:37<00:00,  6.66it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  98%|▉| 251/256 [00:37<00:00,  6.67it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  98%|▉| 252/256 [00:37<00:00,  6.68it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  99%|▉| 253/256 [00:37<00:00,  6.70it/s, loss=0.00069, v_num=3, trai
Epoch 3749:  99%|▉| 254/256 [00:37<00:00,  6.71it/s, loss=0.00069, v_num=3, trai
Epoch 3749: 100%|▉| 255/256 [00:37<00:00,  6.72it/s, loss=0.00069, v_num=3, trai
Epoch 3749: 100%|█| 256/256 

## Inference

In [2]:
import pandas as pd

#Read in your csv and assign it to the variable RR
# 2nd scan
RR = pd.read_csv('/home/jake/projects/dhr/Primno_abyssalis_FEG221101_359_corneas_estimating_resampling_ratio.csv')

RR

index  axis-0      axis-1      axis-2
0     0.0   656.0  471.466616  533.350246
1     1.0   656.0  514.599843  511.783633
2     2.0   656.0  538.367131  482.294590
3     3.0   656.0  432.734739  548.314835
4     4.0   671.0  431.414334  580.004553
5     5.0   671.0  465.744862  566.360369
6     6.0   671.0  502.716199  541.712811
7     7.0   671.0  536.606591  515.744848
8     8.0   705.0  454.741487  605.972515
9     9.0   705.0  495.674039  582.645362
10   10.0   705.0  529.124296  557.117534
11   11.0   705.0  557.292934  530.709436
12   12.0   726.0  437.136089  629.299669
13   13.0   726.0  481.149585  613.454810
14   14.0   726.0  521.201867  587.046712
15   15.0   726.0  548.490235  562.839289
16   16.0   726.0  577.539143  539.072001

In [4]:
from scipy.spatial import distance_matrix

coordinates = RR[['axis-0', 'axis-1', 'axis-2']].values
dist_matrix = distance_matrix(coordinates, coordinates) #Create a distance matrix between points
import numpy as np
np.fill_diagonal(dist_matrix, np.inf)

# Find the nearest neighbor distance for each point
nearest_distances = np.min(dist_matrix, axis=1)

# Add the nearest distances to the dataframe
RR['nearest_distance'] = nearest_distances
RR
mean_nearest_distance = RR['nearest_distance'].mean()
mean_nearest_distance
resample_ratio = mean_nearest_distance/10
resample_ratio #Print your RR; use this to make your inference 

3.290426824776052

In [4]:
# Inferences with version 1 (bad, model not used)
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_1/ -rr 3.290426824776052 -nx 1 -ny 1 -nz 1 -ipmv 0.5 -at 0.5
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_1/ -rr 3.290426824776052 -nx 1 -ny 1 -nz 1 -ipmv 0.5 -at 0.1


TorchIO version: 0.18.88
Running setup!
Found 2 labelled images with labels in ./dataset/primno_corneas/whole/train_images_10/ and ./dataset/primno_corneas/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/primno_corneas/whole/train_images_10/ and ./dataset/primno_corneas/whole/train_labels_10/ for analysis
Training:   2
Validation:  2
Test:       2
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_length': 9, 'batch_size': 2, "
 "'config_stem': 'primno_corneas', 'correct_prediction_distance': 6, "
 "'debug_plots': False, 'double_channels_with_depth': True, 'dropout': "
 "0.0175756794552526, 'heatmap_max_length': 64, 'histogram_landmarks_pat

In [2]:
# Infernces with version 3
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.1 -at 0.05
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.1 -at 0.01
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.1 -at 0.5
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.1 -at 0.4
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.5 -at 0.5 --infer_with_max_filter_fun
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.4 -at 0.5 --infer_with_max_filter_fun
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.3 -at 0.5 --infer_with_max_filter_fun
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.2 -at 0.5 --infer_with_max_filter_fun
# !python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 2 -ny 2 -nz 2 -ipmv 0.1 -at 0.5 --infer_with_max_filter_fun # best so far
!python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 3 -ny 3 -nz 3 -ipmv 0.5 -at 0.5 --infer_with_max_filter_fun
!python main.py infer configs/primno_corneas.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m ./logs/primno_corneas/lightning_logs/version_3/ -rr 3.290426824776052 -nx 3 -ny 3 -nz 3 -ipmv 0.1 -at 0.5 --infer_with_max_filter_fun


TorchIO version: 0.18.88
Running setup!
Found 2 labelled images with labels in ./dataset/primno_corneas/whole/train_images_10/ and ./dataset/primno_corneas/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/primno_corneas/whole/train_images_10/ and ./dataset/primno_corneas/whole/train_labels_10/ for analysis
Training:   2
Validation:  2
Test:       2
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_length': 9, 'batch_size': 2, "
 "'config_stem': 'primno_corneas', 'correct_prediction_distance': 6, "
 "'debug_plots': False, 'double_channels_with_depth': True, 'dropout': "
 "0.0175756794552526, 'heatmap_max_length': 64, 'histogram_landmarks_pat

Rotating volume back to original orientation...


100%|█████████████████████████████████████████████| 3/3 [00:11<00:00,  3.79s/it]

                                                                                
 33%|███████████████                              | 1/3 [00:11<00:22, 11.35s/it]

  0%|                                                     | 0/3 [00:00<?, ?it/s]
Running inference with 60° rotation along the x-axis (2/3),
60° rotation along the y-axis (2/3)
and 0° rotation along the z-axis (1/3)
Creating sampler and applying transform to image...
Initialising patch_loader and aggregator...
Starting inference...



  0%|                                                     | 0/6 [00:00<?, ?it/s]


 17%|███████▌                                     | 1/6 [00:00<00:02,  1.96it/s]


 33%|███████████████                              | 2/6 [00:01<00:02,  1.99it/s]


 50%|██████████████████████▌                      | 3/6 [00:01<00:01,  2.01it/s]


 67%|██████████████████████████████ 

Rotating volume back to original orientation...


 33%|███████████████                              | 1/3 [00:03<00:07,  3.88s/it]
Running inference with 120° rotation along the x-axis (3/3),
0° rotation along the y-axis (1/3)
and 60° rotation along the z-axis (2/3)
Creating sampler and applying transform to image...
Initialising patch_loader and aggregator...
Starting inference...



  0%|                                                     | 0/6 [00:00<?, ?it/s]


 17%|███████▌                                     | 1/6 [00:00<00:02,  1.80it/s]


 33%|███████████████                              | 2/6 [00:01<00:02,  1.87it/s]


 50%|██████████████████████▌                      | 3/6 [00:01<00:01,  1.90it/s]


 67%|██████████████████████████████               | 4/6 [00:02<00:01,  1.92it/s]


 83%|█████████████████████████████████████▌       | 5/6 [00:02<00:00,  1.93it/s]


100%|█████████████████████████████████████████████| 6/6 [00:02<00:00,  2.14it/s]
Rotating volume back to original 

TorchIO version: 0.18.88
Running setup!
Found 2 labelled images with labels in ./dataset/primno_corneas/whole/train_images_10/ and ./dataset/primno_corneas/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/primno_corneas/whole/train_images_10/ and ./dataset/primno_corneas/whole/train_labels_10/ for analysis
Training:   2
Validation:  2
Test:       2
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_length': 9, 'batch_size': 2, "
 "'config_stem': 'primno_corneas', 'correct_prediction_distance': 6, "
 "'debug_plots': False, 'double_channels_with_depth': True, 'dropout': "
 "0.0175756794552526, 'heatmap_max_length': 64, 'histogram_landmarks_pat

In [7]:
import napari
import numpy as np
import torchio as tio


image_path = '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii'
image = tio.ScalarImage(image_path)

# heatmap_path = '/media/jake/Removable backup/Jake/projects/dhr/output/FEG20190213_010.logs_cystisoma_rhabdoms_lightning_logs_version_17_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction.nii'
heatmap_path = '/home/jake/projects/dhr/output/Primno_abyssalis_FEG221101_359.logs_primno_corneas_lightning_logs_version_3_checkpoints_last_x_2_y_2_z_2_average_threshold_0.5_prediction.nii'

#Make sure to use resampled space csv here.
# y_hat_path = '/media/jake/Removable backup/Jake/projects/dhr/output/FEG20190213_010.logs_cystisoma_rhabdoms_lightning_logs_version_17_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction_peak_min_val_0_5_method_center_of_mass.resampled_space_peaks.csv'
y_hat_path = '/home/jake/projects/dhr/output/Primno_abyssalis_FEG221101_359.logs_primno_corneas_lightning_logs_version_3_checkpoints_last_x_2_y_2_z_2_average_threshold_0.5_prediction_peak_min_val_0_4_method_max_filter.resampled_space_peaks.csv'

heatmap = tio.ScalarImage(heatmap_path)


viewer = napari.view_image(heatmap.numpy(), name='heatmap', contrast_limits=[0, 1])
# viewer.add_image(image.numpy(), name='image') #If you want to view your scan also (not necessary)

# load the coordinates to analyse
def load_coordinates(path, flip_axes=False, mct_path=None):
    locations = np.loadtxt(
        path,
        delimiter=',',
        ndmin=2,
        dtype=np.float64
    )
    if not flip_axes: 
        return locations.tolist()

    if not mct_path:
        raise Exception('You must specify `mct_path` if you need to flip_axes')

    mct = tio.ScalarImage(mct_path)
    locations[:,0] = mct.shape[1] - locations[:,0]
    locations[:,1] = mct.shape[2] - locations[:,1]

    return locations.tolist()


y_hat = load_coordinates(y_hat_path)


viewer.add_points(y_hat)

<Points layer 'Points' at 0x7fb9a59c8a90>

# Primno rhabdoms 

## Generating the dataset

The next couple kernels are to manually convert mat files into csv files with rhabdoms points. If you do not need to convert manually you can use `!python mctv_to_csv.py`.

In [2]:
# To convert mat for Primno_abyssalis_FEG221018_356 into rhabdoms raw labels csv
import h5py
import pandas as pd
import os

with h5py.File('/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_356/Primno_abyssalis_356_eye.mat', 'r') as file:
    marked_data = file['save_dat/data/marked'][:]  # Load the entire marked dataset

marked_df = pd.DataFrame(marked_data)


columns_to_keep = marked_df.iloc[5].isin([1, 3, 5, 7]) # correct indices for rhabdoms
column_indices = marked_df.columns[columns_to_keep]
filtered_df = marked_df.iloc[:3, column_indices]
transposed_df = filtered_df.transpose()

# Specify the directory where you want to save the CSV
save_directory = '/home/jake/projects/dhr/dataset/raw_labels'  
csv_name = 'Primno_abyssalis_FEG221018_356_labels_rhaddoms.csv'

csv_path = os.path.join(save_directory, csv_name)

os.makedirs(save_directory, exist_ok=True)

transposed_df.to_csv(csv_path, header=False, index=False)


In [3]:
# To convert mat for Primno_abyssalis_FEG221018_357 into rhabdoms raw labels csv
import h5py
import pandas as pd
import os

with h5py.File('/media/jake/Removable backup/Jake/projects/mctv_resfiles/hyperiids/Primno_abyssalis_FEG221018_357/Primno_abyssalis_357.mat', 'r') as file:
    marked_data = file['save_dat/data/marked'][:]  

marked_df = pd.DataFrame(marked_data)


columns_to_keep = marked_df.iloc[5].isin([1, 3, 5, 7]) # correct indices for rhabdoms
column_indices = marked_df.columns[columns_to_keep]
filtered_df = marked_df.iloc[:3, column_indices]
transposed_df = filtered_df.transpose()

# Specify directory path
save_directory = '/home/jake/projects/dhr/dataset/raw_labels'  
csv_name = 'Primno_abyssalis_FEG221018_357_labels_rhabdoms.csv' # name csv 


csv_path = os.path.join(save_directory, csv_name)


os.makedirs(save_directory, exist_ok=True)


transposed_df.to_csv(csv_path, header=False, index=False)


In [1]:
!python generate_dataset.py -h

usage: generate_dataset.py [-h]
                           [--voxel_spacings VOXEL_SPACINGS [VOXEL_SPACINGS ...]]
                           [--label_name LABEL_NAME]
                           [--crop_label_names CROP_LABEL_NAMES [CROP_LABEL_NAMES ...]]
                           [--patch_size PATCH_SIZE]
                           [--crop_buffer CROP_BUFFER] [--debug]
                           data_source_specifier_path

Generate nicely resampled and formatted images and labels from the datas raw
format.

positional arguments:
  data_source_specifier_path
                        The path to your .csv file that specifies where your
                        images and labels are and whether it should be used
                        for training or testing. This .csv file should have
                        the following columns: 1. image_file_path (path to the
                        dicom or nifti file used to annotate with mctv) 2.
                        labels_<YOUR_LABEL_NAME> (pa

In [4]:
!python generate_dataset.py ./data_source_specifiers/primno_rhabdoms.csv -l rhabdoms -v 10 -cl rhabdoms -cb 16

Processing images with voxel spacing 10
  0%|                                                     | 0/2 [00:00<?, ?it/s]Starting conversion of /media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f356_u0000000/Primno_abyssalis_FEG221018_356.nii
Cropping to edges of crop_labels with buffer
Resampling the image
/home/jake/projects/dhr/generate_dataset.py:178: UserWarning: You are reducing the size of your volume by 0.4776034069109001. Ensure that you want such a small volume. Consider changing your `v` parameter.
  warnings.warn(
Resampling image by ratio: 2.093787409239642
Image old spacing (1.0, 1.0, 1.0)
Image new spacing (2.093787409239642, 2.093787409239642, 2.093787409239642)
Resampling labels by ratio: 2.093787409239642
Resampling crop area labels by ratio: 2.093787409239642
saving 8 patches...

100%|█████████████████████████████████████████████| 8/8 [00:00<00:00,  8.48it/s]
finished saving
 50%|██████████████████████▌                    

## Checking

In [3]:
!python check_data.py -h

usage: check_data.py [-h] [--n_plot_at_once N_PLOT_AT_ONCE] [--check-loading]
                     config_path

positional arguments:
  config_path           The path to the config file. Example:
                        configs/fiddlercrab_cornea_config.yaml

options:
  -h, --help            show this help message and exit
  --n_plot_at_once N_PLOT_AT_ONCE
                        The number of images to plot at once.
  --check-loading       Check loading of all images and labels, but don't plot
                        anything. Can be useful if you just want to make sure
                        everything loads correctly. Will print an error
                        message if a image or label does not load correctly.


In [10]:
!python check_data.py ./configs/primno_rhabdoms.yaml

Running setup!
Found 2 labelled images with labels in ./dataset/primno_rhabdoms/whole/train_images_10/ and ./dataset/primno_rhabdoms/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/primno_rhabdoms/whole/train_images_10/ and ./dataset/primno_rhabdoms/whole/train_labels_10/ for analysis
("Initiating model using the following config: {'seed': 44, 'lr': "
 "0.0424937961824346, 'num_steps': 1100000, 'weight_decay': "
 "1.52709371682483e-06, 'momentum': 0.510999549987835, 'nesterov': False, "
 "'act': 'ReLU', 'output_activation': 'None', 'softargmax': False, "
 "'num_encoding_blocks': 5, 'out_channels_first_layer': 32, "
 "'double_channels_with_depth': True, 'pooling_type': 'max', "
 "'upsampling_type': 'conv

## Training

In [13]:
# Version 1
# !python main.py train configs/primno_rhabdoms.yaml -w ./logs/cystisoma_rhabdoms/lightning_logs/version_19/checkpoints/epoch=1779-step=1004321.ckpt -ne 10
# Version 3 (changed starting sigma to 1.5 and peak min to 0.3 )
!python main.py train configs/primno_rhabdoms.yaml -w ./logs/cystisoma_rhabdoms/lightning_logs/version_19/checkpoints/epoch=1684-step=998241.ckpt -ne 10


TorchIO version: 0.18.88
("Initiating model using the following config: {'seed': 44, 'lr': "
 "0.0424937961824346, 'num_steps': 1100000, 'weight_decay': "
 "1.52709371682483e-06, 'momentum': 0.510999549987835, 'nesterov': False, "
 "'act': 'ReLU', 'output_activation': 'None', 'softargmax': False, "
 "'num_encoding_blocks': 5, 'out_channels_first_layer': 32, "
 "'double_channels_with_depth': True, 'pooling_type': 'max', "
 "'upsampling_type': 'conv', 'dropout': 0.0175756794552526, "
 "'loss_in_sigma_space': False, 'debug_plots': False, 'mse_with_f1': False, "
 "'visualise_model': False, 'learn_sigma': False, 'optimiser': 'SGD', "
 "'pin_memory': False, 'train_images_dir': "
 "'./dataset/primno_rhabdoms/whole/train_images_10/', 'train_labels_dir': "
 "'./dataset/primno_rhabdoms/whole/train_labels_10/', 'test_images_dir': "
 "'./dataset/primno_rhabdoms/whole/train_images_10/', 'test_labels_dir': "
 "'./dataset/primno_rhabdoms/whole/train_labels_10/', 'image_suffix': 'image', "
 "'label_su

Epoch 1689: : 165it [01:59,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 166it [02:00,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 167it [02:01,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 168it [02:01,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 169it [02:02,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 170it [02:03,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 171it [02:03,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 172it [02:04,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 173it [02:05,  1.38it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 174it [02:05,  1.39it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 175it [02:06,  1.39it/s, loss=0.000524, v_num=3, train_loss=0.000578]
Epoch 1689: : 176it [02:06,  1.39it/s, loss=0.000524, v_num=3, train_loss=0.

Epoch 1699:  51%|▌| 131/256 [01:35<01:31,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  52%|▌| 132/256 [01:36<01:30,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  52%|▌| 133/256 [01:37<01:29,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  52%|▌| 134/256 [01:37<01:29,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  53%|▌| 135/256 [01:38<01:28,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  53%|▌| 136/256 [01:39<01:27,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  54%|▌| 137/256 [01:39<01:26,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  54%|▌| 138/256 [01:40<01:25,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  54%|▌| 139/256 [01:41<01:25,  1.37it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  55%|▌| 140/256 [01:41<01:24,  1.38it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  55%|▌| 141/256 [01:42<01:23,  1.38it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  55%|▌| 142/256 [01:43<01:22,  1.38it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  56%|▌| 143/256 

Epoch 1699:  89%|▉| 228/256 [02:39<00:19,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  89%|▉| 229/256 [02:40<00:18,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  90%|▉| 230/256 [02:41<00:18,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  90%|▉| 231/256 [02:41<00:17,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  91%|▉| 232/256 [02:42<00:16,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  91%|▉| 233/256 [02:43<00:16,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  91%|▉| 234/256 [02:43<00:15,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  92%|▉| 235/256 [02:44<00:14,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  92%|▉| 236/256 [02:44<00:13,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  93%|▉| 237/256 [02:45<00:13,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  93%|▉| 238/256 [02:46<00:12,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  93%|▉| 239/256 [02:46<00:11,  1.43it/s, loss=0.00052, v_num=3, trai
Epoch 1699:  94%|▉| 240/256 

Epoch 1709:  76%|▊| 194/256 [02:28<00:47,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  76%|▊| 195/256 [02:29<00:46,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  77%|▊| 196/256 [02:29<00:45,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  77%|▊| 197/256 [02:30<00:45,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  77%|▊| 198/256 [02:31<00:44,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  78%|▊| 199/256 [02:31<00:43,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  78%|▊| 200/256 [02:32<00:42,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  79%|▊| 201/256 [02:33<00:41,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  79%|▊| 202/256 [02:33<00:41,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  79%|▊| 203/256 [02:34<00:40,  1.31it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  80%|▊| 204/256 [02:35<00:39,  1.32it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  80%|▊| 205/256 [02:35<00:38,  1.32it/s, loss=0.000549, v_num=3, tra
Epoch 1709:  80%|▊| 206/256 

...

Epoch 1759:  85%|▊| 218/256 [02:41<00:28,  1.35it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  86%|▊| 219/256 [02:42<00:27,  1.35it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  86%|▊| 220/256 [02:43<00:26,  1.35it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  86%|▊| 221/256 [02:43<00:25,  1.35it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  87%|▊| 222/256 [02:44<00:25,  1.35it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  87%|▊| 223/256 [02:44<00:24,  1.35it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  88%|▉| 224/256 [02:45<00:23,  1.35it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  88%|▉| 225/256 [02:46<00:22,  1.35it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  88%|▉| 226/256 [02:46<00:22,  1.36it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  89%|▉| 227/256 [02:47<00:21,  1.36it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  89%|▉| 228/256 [02:47<00:20,  1.36it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  89%|▉| 229/256 [02:48<00:19,  1.36it/s, loss=0.000536, v_num=3, tra
Epoch 1759:  90%|▉| 230/256 

Epoch 1769:  72%|▋| 184/256 [02:20<00:54,  1.31it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  72%|▋| 185/256 [02:20<00:54,  1.31it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  73%|▋| 186/256 [02:21<00:53,  1.31it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  73%|▋| 187/256 [02:22<00:52,  1.32it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  73%|▋| 188/256 [02:22<00:51,  1.32it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  74%|▋| 189/256 [02:23<00:50,  1.32it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  74%|▋| 190/256 [02:23<00:50,  1.32it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  75%|▋| 191/256 [02:24<00:49,  1.32it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  75%|▊| 192/256 [02:25<00:48,  1.32it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  75%|▊| 193/256 [02:25<00:47,  1.32it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  76%|▊| 194/256 [02:26<00:46,  1.32it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  76%|▊| 195/256 [02:27<00:45,  1.33it/s, loss=0.000567, v_num=3, tra
Epoch 1769:  77%|▊| 196/256 

Epoch 1779:  59%|▌| 150/256 [02:00<01:24,  1.25it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  59%|▌| 151/256 [02:00<01:24,  1.25it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  59%|▌| 152/256 [02:01<01:23,  1.25it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  60%|▌| 153/256 [02:02<01:22,  1.25it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  60%|▌| 154/256 [02:02<01:21,  1.25it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  61%|▌| 155/256 [02:03<01:20,  1.26it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  61%|▌| 156/256 [02:03<01:19,  1.26it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  61%|▌| 157/256 [02:04<01:18,  1.26it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  62%|▌| 158/256 [02:05<01:17,  1.26it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  62%|▌| 159/256 [02:05<01:16,  1.26it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  62%|▋| 160/256 [02:06<01:15,  1.27it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  63%|▋| 161/256 [02:06<01:14,  1.27it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  63%|▋| 162/256 

Epoch 1779:  96%|▉| 247/256 [02:59<00:06,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  97%|▉| 248/256 [03:00<00:05,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  97%|▉| 249/256 [03:00<00:05,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  98%|▉| 250/256 [03:01<00:04,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  98%|▉| 251/256 [03:02<00:03,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  98%|▉| 252/256 [03:02<00:02,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  99%|▉| 253/256 [03:03<00:02,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779:  99%|▉| 254/256 [03:03<00:01,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779: 100%|▉| 255/256 [03:04<00:00,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1779: 100%|█| 256/256 [03:05<00:00,  1.38it/s, loss=0.000495, v_num=3, tra
Epoch 1789:  50%|▌| 128/256 [01:46<01:46,  1.21it/s, loss=0.00061, v_num=3, trai
Validation: 0it [00:00, ?it/s]
Validation DataLoader 0:   0%|                          | 0/128 [00:00<?, ?it/

Epoch 1789:  83%|▊| 213/256 [02:46<00:33,  1.28it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  84%|▊| 214/256 [02:47<00:32,  1.28it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  84%|▊| 215/256 [02:47<00:31,  1.28it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  84%|▊| 216/256 [02:48<00:31,  1.28it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  85%|▊| 217/256 [02:48<00:30,  1.28it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  85%|▊| 218/256 [02:49<00:29,  1.29it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  86%|▊| 219/256 [02:50<00:28,  1.29it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  86%|▊| 220/256 [02:50<00:27,  1.29it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  86%|▊| 221/256 [02:51<00:27,  1.29it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  87%|▊| 222/256 [02:52<00:26,  1.29it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  87%|▊| 223/256 [02:52<00:25,  1.29it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  88%|▉| 224/256 [02:53<00:24,  1.29it/s, loss=0.00061, v_num=3, trai
Epoch 1789:  88%|▉| 225/256 

In [21]:
# Version 2
!python main.py train configs/primno_rhabdoms.yaml -w ./logs/paraphronima_rhabdoms_from_pretrained/lightning_logs/version_1/checkpoints/epoch=147-step=890880.ckpt -ne 10


In [14]:
# Version 4
!python main.py train configs/primno_rhabdoms.yaml -w ./logs/paraphronima_rhabdoms/lightning_logs/version_23/checkpoints/epoch=99-step=537600-v1.ckpt -ne 10


In [15]:
# Version 5
python main.py train configs/primno_rhabdoms.yaml -w ./logs/fiddlercrab_rhabdoms/lightning_logs/version_10/checkpoints/epoch=67-step=591872.ckpt -ne 10


## Inference

In [ ]:
import torchio as tio

image_path = '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii'
image = tio.ScalarImage(image_path)

# view file with napari
import napari


viewer = napari.view_image(image.numpy(), name='image')

In [ ]:
import pandas as pd

RR = pd.read_csv('/home/jake/projects/dhr/Primno_abyssalis_FEG221101_359_corneas_estimating_resampling_ratio.csv')

RR

In [ ]:
from scipy.spatial import distance_matrix

coordinates = RR[['axis-0', 'axis-1', 'axis-2']].values
dist_matrix = distance_matrix(coordinates, coordinates) #Create a distance matrix between points
import numpy as np
np.fill_diagonal(dist_matrix, np.inf)

# Find the nearest neighbor distance for each point
nearest_distances = np.min(dist_matrix, axis=1)

# Add the nearest distances to the dataframe
RR['nearest_distance'] = nearest_distances
RR
mean_nearest_distance = RR['nearest_distance'].mean()
mean_nearest_distance
resample_ratio = mean_nearest_distance/10
resample_ratio #Print your RR; use this to make your inference 

In [6]:
!python main.py infer -h

usage: main.py [-h] [--volume_path VOLUME_PATH]
               [--sql_storage_url SQL_STORAGE_URL]
               [--starting_weights_path STARTING_WEIGHTS_PATH]
               [--model_path MODEL_PATH] [--profile] [--num_steps NUM_STEPS]
               [--check_val_every_n_epoch CHECK_VAL_EVERY_N_EPOCH]
               [--resample_ratio_path RESAMPLE_RATIO_PATH]
               [--bbox_path BBOX_PATH] [--n_x_dirs N_X_DIRS]
               [--n_y_dirs N_Y_DIRS] [--n_z_dirs N_Z_DIRS]
               [--resample_ratio RESAMPLE_RATIO] [--already_resampled]
               [--training_data_histogram] [--infer_with_max_filter_fun]
               [--average_threshold AVERAGE_THRESHOLD]
               [--inference_peak_min_val INFERENCE_PEAK_MIN_VAL]
               {train,tune,infer,locate_peaks} config_path

Train, hyperparameter tune or infer with a deep heatmap regression model

positional arguments:
  {train,tune,infer,locate_peaks}
                        Mode of operation
  config_path      

In [8]:
# Inferences on version 1
# !python main.py infer configs/primno_rhabdoms.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m /media/jakes-hd/logs/primno_rhabdoms/lightning_logs/version_1 -rr 2.9493045478545903 -nx 1 -ny 1 -nz 1 -ipmv 0.5 -at 0.5 --infer_with_max_filter_fun
!python main.py infer configs/primno_rhabdoms.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m /media/jakes-hd/logs/primno_rhabdoms/lightning_logs/version_1 -rr 2.9493045478545903 -nx 1 -ny 1 -nz 1 -ipmv 0.1 -at 0.1 


TorchIO version: 0.18.88
Running setup!
Found 2 labelled images with labels in ./dataset/primno_rhabdoms/whole/train_images_10/ and ./dataset/primno_rhabdoms/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/primno_rhabdoms/whole/train_images_10/ and ./dataset/primno_rhabdoms/whole/train_labels_10/ for analysis
Training:   2
Validation:  2
Test:       2
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_length': 9, 'batch_size': 2, "
 "'config_stem': 'primno_rhabdoms', 'correct_prediction_distance': 6, "
 "'debug_plots': False, 'double_channels_with_depth': True, 'dropout': "
 "0.0175756794552526, 'heatmap_max_length': 64, 'histogram_landmark

In [8]:
# !python main.py infer configs/primno_rhabdoms.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m /media/jakes-hd/logs/primno_rhabdoms/lightning_logs/version_2 -rr 2.9493045478545903 -nx 2 -ny 2 -nz 2 -ipmv 0.1 -at 0.1 #--infer_with_max_filter_fun
# (best)
# !python main.py infer configs/primno_rhabdoms.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m /media/jakes-hd/logs/primno_rhabdoms/lightning_logs/version_2 -rr 2.9493045478545903 -nx 2 -ny 2 -nz 2 -ipmv 0.1 -at 0.5 --infer_with_max_filter_fun
!python main.py infer configs/primno_rhabdoms.yaml -v '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii' -m /media/jakes-hd/logs/primno_rhabdoms/lightning_logs/version_2 -rr 2.9493045478545903 -nx 2 -ny 2 -nz 2 -ipmv 0.2 #-at 0.5 --infer_with_max_filter_fun


TorchIO version: 0.18.88
Running setup!
Found 2 labelled images with labels in ./dataset/primno_rhabdoms/whole/train_images_10/ and ./dataset/primno_rhabdoms/whole/train_labels_10/ for analysis
/home/jake/projects/dhr/deep_radiologist/lightning_modules.py:383: UserWarning: Length of validation subjects is 0. Setting the validation subjects to the same subjects as those used in training. Saved metrics/logs may be misleading.
  warnings.warn(
Found 2 labelled images with labels in ./dataset/primno_rhabdoms/whole/train_images_10/ and ./dataset/primno_rhabdoms/whole/train_labels_10/ for analysis
Training:   2
Validation:  2
Test:       2
("Initiating model using the following config: {'act': 'ReLU', "
 "'balanced_sampler': True, 'balanced_sampler_max_length': 9, 'batch_size': 2, "
 "'config_stem': 'primno_rhabdoms', 'correct_prediction_distance': 6, "
 "'debug_plots': False, 'double_channels_with_depth': True, 'dropout': "
 "0.0175756794552526, 'heatmap_max_length': 64, 'histogram_landmark

Initialising patch_loader and aggregator...
Starting inference...



  0%|                                                    | 0/12 [00:00<?, ?it/s]


  8%|███▋                                        | 1/12 [00:00<00:06,  1.83it/s]


 17%|███████▎                                    | 2/12 [00:01<00:05,  1.86it/s]


 25%|███████████                                 | 3/12 [00:01<00:04,  1.88it/s]


 33%|██████████████▋                             | 4/12 [00:02<00:04,  1.88it/s]


 42%|██████████████████▎                         | 5/12 [00:02<00:03,  1.89it/s]


 50%|██████████████████████                      | 6/12 [00:03<00:03,  1.89it/s]


 58%|█████████████████████████▋                  | 7/12 [00:03<00:02,  1.89it/s]


 67%|█████████████████████████████▎              | 8/12 [00:04<00:02,  1.88it/s]


 75%|█████████████████████████████████           | 9/12 [00:04<00:01,  1.89it/s]


 83%|███████████████████████████████████▊       | 10/12 [00:05<00:01,  1.89it/s]


 92%|█████████████

 92%|███████████████████████████████████████▍   | 11/12 [00:05<00:00,  1.88it/s]


100%|███████████████████████████████████████████| 12/12 [00:06<00:00,  1.89it/s]
Rotating volume back to original orientation...


100%|█████████████████████████████████████████████| 2/2 [00:15<00:00,  7.75s/it]

                                                                                
Running inference in 8 direction/s: 100%|█████████| 2/2 [01:02<00:00, 31.03s/it]
Average was calculated while running. Returning this average.
Saving prediction to ./output/Primno_abyssalis_FEG221101_359..._.._.._.._media_jakes-hd_logs_primno_rhabdoms_lightning_logs_version_2_checkpoints_last_x_2_y_2_z_2_average_threshold_None_prediction.nii
Locating peaks...
Saving peaks in resampled space...
saving to output/Primno_abyssalis_FEG221101_359..._.._.._.._media_jakes-hd_logs_primno_rhabdoms_lightning_logs_version_2_checkpoints_last_x_2_y_2_z_2_average_threshold_None_prediction_peak_min_val_0_2_method_center_of_mass.res

In [57]:
import napari
import numpy as np
import torchio as tio


image_path = '/media/jake/Removable backup/Dropbox/Full body hyperiid scans/Head Scans_nifti/Primno_abyssalis_f359_u0000000/Primno_abyssalis_FEG221101_359.nii'
image = tio.ScalarImage(image_path)

# heatmap_path = '/media/jake/Removable backup/Jake/projects/dhr/output/FEG20190213_010.logs_cystisoma_rhabdoms_lightning_logs_version_17_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction.nii'
heatmap_path = '/media/jake/Removable backup/Jake/projects/dhr/output/Primno_abyssalis_FEG221101_359.logs_primno_rhabdoms_lightning_logs_version_2_checkpoints_last_x_2_y_2_z_2_average_threshold_0.5_prediction.nii'

#Make sure to use resampled space csv here.
# y_hat_path = '/media/jake/Removable backup/Jake/projects/dhr/output/FEG20190213_010.logs_cystisoma_rhabdoms_lightning_logs_version_17_checkpoints_last_x_3_y_3_z_3_average_threshold_0.5_prediction_peak_min_val_0_5_method_center_of_mass.resampled_space_peaks.csv'
y_hat_path = '/media/jake/Removable backup/Jake/projects/dhr/output/Primno_abyssalis_FEG221101_359.logs_primno_rhabdoms_lightning_logs_version_2_checkpoints_last_x_2_y_2_z_2_average_threshold_0.5_prediction_peak_min_val_0_1_method_max_filter.resampled_space_peaks.csv'
heatmap = tio.ScalarImage(heatmap_path)


viewer = napari.view_image(heatmap.numpy(), name='heatmap', contrast_limits=[0, 1])
# viewer.add_image(image.numpy(), name='image') #If you want to view your scan also (not necessary)

# load the coordinates to analyse
def load_coordinates(path, flip_axes=False, mct_path=None):
    locations = np.loadtxt(
        path,
        delimiter=',',
        ndmin=2,
        dtype=np.float64
    )
    if not flip_axes: 
        return locations.tolist()

    if not mct_path:
        raise Exception('You must specify `mct_path` if you need to flip_axes')

    mct = tio.ScalarImage(mct_path)
    locations[:,0] = mct.shape[1] - locations[:,0]
    locations[:,1] = mct.shape[2] - locations[:,1]

    return locations.tolist()


y_hat = load_coordinates(y_hat_path)


viewer.add_points(y_hat)